In [0]:
!pip install openpyxl

from pyspark.sql.functions import current_timestamp, current_date, concat, month, col, lit, when, round, floor, date_format, to_date, countDistinct, avg, sum, date_trunc, lag, min, array_contains, count
from pyspark.sql.types import LongType, DoubleType
from pyspark.sql.window import Window

import pandas as pd
import openpyxl
import itertools
import requests


[notice] A new release of pip available: 22.2.2 -> 25.1.1
[notice] To update, run: pip install --upgrade pip


In [0]:
pip install presto-python-client 

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [0]:
import pandas as pd
import prestodb
import numpy as np
import datetime
from pyspark.sql import SparkSession

In [0]:
!pip install dotenv


In [0]:
from dotenv import load_dotenv, find_dotenv
import os

# env_path = find_dotenv()

env_path = "/Workspace/Users/sheetal.suwalka@delhivery.com/.env"

print("Loading .env from:", env_path)
load_dotenv(dotenv_path=env_path, override=True)

Auth_token_key = os.getenv("Presto_query_authenticate_token")
user = os.getenv("user")
port = os.getenv("port")
host = os.getenv("host")

import prestodb

conn = prestodb.dbapi.connect(
        host=host,
        port=port,
        user = user,
        source='rstudio',
        catalog="awsdatacatalog",
        schema="express_dwh",
        http_scheme="http",
        http_headers = { "Authorization": f'''Bearer {Auth_token_key}'''})


In [0]:
# conn = prestodb.dbapi.connect(
#         host='trino.delhivery.com',
#         port=8889,
#         user='r-studio-us-east',
#         source='rstudio',
#         catalog='awsdatacatalog',
#         schema='express_dwh'
#         ) 


In [0]:
# Create a SparkSession
spark = SparkSession.builder \
    .appName("example") \
    .config("spark.sql.parquet.mergeSchema", "true") \
    .getOrCreate() 

In [0]:
from datetime import datetime, timedelta

import pytz

# Define IST timezone
ist = pytz.timezone('Asia/Kolkata')

# Get current time in IST
current_time_ist = datetime.now(ist)
current_date = current_time_ist.strftime("%Y-%m-%d") 


print(current_date)

2025-05-21


In [0]:

# ad = '2025-02-28'
# start_date = '2025-03-03'
# end_date = '2025-03-09'
# ad2 = '2025-03-12'

# ad = '2025-04-18'
# start_date = '2025-04-21'
# end_date = '2025-04-27'
# ad2 = '2025-04-30'

ad = '2025-05-25'
start_date = '2025-06-01'
end_date = '2025-06-10'
ad2 = '2025-06-14'

# ad = '2025-01-15'
# start_date = '2025-01-20'
# end_date = '2025-01-26'


In [0]:
wbn_jrny_query = f'''
 with wbn_journey as (
    select c.*, a.property_facility_name as origin_facility_name, b.property_facility_name as consignee_facility_name
    from
    (select wbn, mwn,
    trid trip_uuid,
    cs_ss as type,
    cs_sr as action_performed,
    -- date_dlvdt + interval '330' minute delivery_time, 
    cs_sd + interval '330' minute scan_time,
    cs_sl as current_scan_location,
    cs_slid as current_scan_loc_id,
    cs_nsl,
    cs_st,
    ocid,
    cnid,
    oc,
    cn,
    case when bzn = 'A' then 'A' 
    when bzn = 'B' then 'B' 
    when bzn in ('C','C1','C2') then 'C' 
    when bzn in ('D','D1','D2') then 'D'
    else bzn end as bzn ,
    from_unixtime(action_date/1000000.0) + interval '330' minute action_time,
    cs_source_bs,
    bag_bs,
    cast(date_cpd + INTERVAL '330' MINUTE  as TIMESTAMP) AS pickup_date,
    CAST(fpd + INTERVAL '330' MINUTE AS TIMESTAMP) as first_pending_date
    from express_dwh.package_s3_parquet
    where 
    ad >= date_format(cast('{ad}' as date), '%Y-%m-%d-%H')
     and ad <= date_format(cast('{ad2}' as date), '%Y-%m-%d-%H')
    and date(date_cpd + interval '330' minute) >= cast('{start_date}' as date)
    and date(date_cpd + interval '330' minute) <= cast('{end_date}' as date)

    -- ad >= date_format((CURRENT_DATE - interval '10' DAY), '%Y-%m-%d-%H')
    -- and date(date_cpd + interval '330' minute) >= (CURRENT_DATE  - interval '7' DAY)
    -- and date(date_cpd + interval '330' minute) <= (CURRENT_DATE   - interval '1' DAY)
    and  pdt not IN ('Heavy', 'Flash_Heavy', 'B2B')
    and mot not in ('E')
    -- and oc like '%_GW%'
    -- and oc not in ('Gurgaon_Tauru_GW (Haryana)', 'Delhi_Airport_GW (Delhi)', 'Noida_Bairangpur_GW (Uttar Pradesh)')
     and oc in ('Gurgaon_Tauru_GW (Haryana)', 'Delhi_Airport_GW (Delhi)', 'Noida_Bairangpur_GW (Uttar Pradesh)',
         'Bhiwandi_Lonad_GW (Maharashtra)','Faridabad_MathuraRoad_GW (Haryana)','Bangalore_Hoskote_GW (Karnataka)', 'Kolkata_Dankuni_GW (West Bengal)','Ahmedabad_Kanera_GW (Gujarat)', 'Indore_Dakachya_GW (Madhya Pradesh)','Hyderabad_Medchal_GW (Telangana)','Surat_Kacholi_GW (Gujarat)','Jaipur_Sez_GW (Rajasthan)','Chennai_Sriperumbudur_GW (Tamil Nadu)','Pune_Sudhwadi_GW (Maharashtra)', 'Surat_Varachha_C (Gujarat)','Surat_Laldarwaja1_C (Gujarat)','Surat_RingRd_C (Gujarat)','Rajkot_Amargadh_H (Gujarat)','Jaipur_Mansrover_C (Rajasthan)','Gurgaon_PalamVihar_C (Haryana)','Bangalore_Nelamangla_H (Karnataka)','Mumbai_AshokNagar_C (Maharashtra)','Panipat_Diwana_P (Haryana)','Hisar_Dabra_H (Haryana)','Sagar_Pagara_P (Madhya Pradesh)')

    and bzn in ('A','B','C','C1','C2','D','D1','D2')

    order by wbn, action_date) c
    left join  hudi_db.hudi_facility_parquet a on c.ocid = a.property_facility_facility_code
    left join  hudi_db.hudi_facility_parquet b on c.cnid = b.property_facility_facility_code
      
)

, fm_last_scan_time_df as (
select wbn, max(scan_time) as fm_last_scan_time
from
(select *
 from wbn_journey
 where current_scan_location = oc 
 and cs_st = 'UD'
 and action_performed != 'Vehicle delayed' and lower(action_performed) not like '%delay%'
 order by wbn, action_time)
 group by wbn)

, wbn_first_last_trip_loc as (
     select distinct * from
     (select distinct wbn, trip_uuid,cs_st, first_value(current_scan_loc_id) over(partition by wbn, trip_uuid order by scan_time) as first_center_id,
last_value(current_scan_loc_id) over(partition by wbn, trip_uuid order by scan_time) as last_center_id
     from wbn_journey
     where   cs_st = 'UD')
     where trip_uuid is not null and first_center_id != last_center_id 

 )

, wbn_journey_till_cn as (

    select a.*
     from wbn_journey a
    join (select distinct wbn, first_pending_date from wbn_journey where first_pending_date is not null) b
    on a.wbn = b.wbn and a.scan_time <= b.first_pending_date

)

, wbn_journey_top_path as 
(select distinct bzn_t, origin_facility_name_t, consignee_facility_name_t, wbn_jounrney_path_t
from
(select bzn as bzn_t, origin_facility_name as origin_facility_name_t, consignee_facility_name as consignee_facility_name_t, wbn_jounrney_path as wbn_jounrney_path_t,  wbn_count, rank() over(partition by bzn, origin_facility_name, consignee_facility_name order by wbn_count desc) as rank_wbn_journey
from 
(select bzn, origin_facility_name, consignee_facility_name, wbn_jounrney_path, count(distinct wbn) as wbn_count 
from 
(select wbn, bzn, origin_facility_name, consignee_facility_name,
ARRAY_DISTINCT(ARRAY_AGG(current_scan_location ORDER BY min_scan_time)) as wbn_jounrney_path
from
(select  wbn, bzn, origin_facility_name, consignee_facility_name ,current_scan_location, current_scan_loc_id, min(scan_time) as min_scan_time
    from wbn_journey
    where   cs_st = 'UD'
    group by 1,2,3,4,5,6
    )
group by 1,2,3,4 )
group by 1,2,3,4
)
)
where rank_wbn_journey = 1)


, top_path_wbn as
(select a.* 
from
(select wbn as wbn_top_path, bzn as bzn_w, origin_facility_name as origin_facility_name_w, consignee_facility_name as consignee_facility_name_w,
ARRAY_DISTINCT(ARRAY_AGG(current_scan_location ORDER BY min_scan_time)) as wbn_jounrney_path_w
from
(select  wbn, bzn, origin_facility_name, consignee_facility_name ,current_scan_location, current_scan_loc_id, min(scan_time) as min_scan_time
    from wbn_journey
    where   cs_st = 'UD'
    group by 1,2,3,4,5,6
    )
group by 1,2,3,4) a
inner join wbn_journey_top_path b 
on a.bzn_w = b.bzn_t and a.origin_facility_name_w = b.origin_facility_name_t 
and a.consignee_facility_name_w = b.consignee_facility_name_t and a.wbn_jounrney_path_w = b.wbn_jounrney_path_t
)

, wbn_intransit_centers_dwell as 

 ( select wbn, bzn, origin_facility_name, consignee_facility_name, sum(intransit_dwell_in_hours) as sum_intransit_dwell_in_hour
 from
( select wbn, bzn, origin_facility_name, consignee_facility_name, current_scan_location, min_scan_time, max_scan_time,
cast(date_diff('minute', min_scan_time, max_scan_time)/60.00 as double) as intransit_dwell_in_hours
from 
(
    select distinct  wbn , bzn, origin_facility_name, consignee_facility_name, current_scan_location, min(scan_time) as min_scan_time, max(scan_time) as max_scan_time
    from (select * from wbn_journey_till_cn where wbn in (select distinct wbn_top_path from top_path_wbn) and action_performed != 'Vehicle delayed' and lower(action_performed) not like '%delay%')a 
    where   cs_st = 'UD' and current_scan_location != oc and current_scan_location != cn
    group by 1,2,3,4,5
)

order by origin_facility_name, consignee_facility_name, min_scan_time
)
 group by 1,2,3,4)

,  od_intransit_centers_dwell as 
 
(select bzn as bzn_i, origin_facility_name as origin_facility_name_i, consignee_facility_name as consignee_facility_name_i,  ARRAY_DISTINCT(ARRAY_AGG(intransit_center_dwell ORDER BY wbn_count desc)) as intransit_centers_and_dwell_in_hour
from

(select bzn, origin_facility_name, consignee_facility_name, wbn_count,avg_intransit_dwell_in_hour_int, concat(current_scan_location, ' - (', cast(avg_intransit_dwell_in_hour as varchar), ' hours) ') as intransit_center_dwell
from

( select bzn, origin_facility_name, consignee_facility_name, current_scan_location,
 format('%.2f', round(sum(intransit_dwell_in_hours)/count(distinct wbn),2)) as avg_intransit_dwell_in_hour, count(distinct wbn) as wbn_count, 
 round(sum(intransit_dwell_in_hours)/count(distinct wbn),2) as avg_intransit_dwell_in_hour_int
 from
( select wbn, bzn, origin_facility_name, consignee_facility_name, current_scan_location, min_scan_time,
cast(date_diff('minute', min_scan_time, max_scan_time)/60.00 as double) as intransit_dwell_in_hours
from 
(
    select distinct  wbn , bzn, origin_facility_name, consignee_facility_name, current_scan_location, min(scan_time) as min_scan_time, max(scan_time) as max_scan_time
    from (select * from wbn_journey_till_cn where wbn in (select distinct wbn_top_path from top_path_wbn) and action_performed != 'Vehicle delayed' and lower(action_performed) not like '%delay%')a 
    where   cs_st = 'UD' and current_scan_location != oc and current_scan_location != cn
    group by 1,2,3,4,5
)

order by origin_facility_name, consignee_facility_name, min_scan_time
)
group by 1,2,3,4
order by 5 desc
)
)
group by 1,2,3 )


,  trips_fms_2 as
( select wbn,  
 ARRAY_AGG(distinct trip_uuid) as trip_uuid_array,  ARRAY_AGG(distinct route_schedule_uuid) as route_id_array, 
sum(trip_duration_in_hours) as total_trip_time from
(select distinct wbn, trip_uuid, route_schedule_uuid, (to_unixtime(first_loc_depart_time) - to_unixtime(trip_start_time)) / 3600 AS trip_duration_in_hours 
from
( select *, lag(first_loc_depart_time) over(PARTITION by wbn, trip_uuid order by first_loc_depart_time ) as trip_start_time
from
(

( select b.wbn, a.trip_uuid , a.route_schedule_uuid,  a.action_performed, first_center_id,  max(trip_time) as first_loc_depart_time
from 
( select 
  distinct  trip_uuid , route_schedule_uuid, action_performed, action_center,
  from_unixtime(action_date/1000000.0) + interval '330' minute trip_time
   FROM
   express_dwh.trips_parquet
   where
   ad >= date_format(cast('{ad}' as date), '%Y-%m-%d-%H')
   and ad <= date_format(cast('{ad2}' as date), '%Y-%m-%d-%H')
  --  ad >= date_format((CURRENT_DATE   - interval '10' DAY), '%Y-%m-%d-%H')
and action_performed in ('Arrived','Departed')
order by trip_time ) a
   left join wbn_first_last_trip_loc b
   on a.trip_uuid = b.trip_uuid and first_center_id = action_center
    where  wbn is not null
    and action_performed in ('Departed')
    and  cs_st = 'UD'
    group by 1,2,3,4,5 )

    union 

( select b.wbn, a.trip_uuid , a.route_schedule_uuid, a.action_performed, last_center_id,  min(trip_time) as last_loc_arrival_time
from 
( select 
  distinct  trip_uuid , route_schedule_uuid, action_performed, action_center,
  from_unixtime(action_date/1000000.0) + interval '330' minute trip_time
   FROM
   express_dwh.trips_parquet
   where
   ad >= date_format(cast('{ad}' as date), '%Y-%m-%d-%H')
   and ad <= date_format(cast('{ad2}' as date), '%Y-%m-%d-%H')
   -- ad >= date_format((CURRENT_DATE  - interval '10' DAY), '%Y-%m-%d-%H')
and action_performed in ('Arrived','Departed')
order by trip_time ) a
   left join wbn_first_last_trip_loc b
   on a.trip_uuid = b.trip_uuid and last_center_id = action_center
    where  wbn is not null
    and action_performed in ('Arrived')
    and  cs_st = 'UD'
    group by 1,2,3,4,5 )
)
)
where trip_start_time is not null)
group by 1)


 select   bzn, origin_facility_name, consignee_facility_name, 
 REGEXP_REPLACE(wbn_jounrney_path, ',',' -> ') as wbn_jounrney_path, intransit_centers_and_dwell_in_hour,  ARRAY_DISTINCT(ARRAY_AGG(distinct trip_uuid_array )) AS trip_uuid_array, ARRAY_DISTINCT(ARRAY_AGG(distinct route_id_array )) AS route_id_array,
count(distinct wbn) as wbn_count, sum(network_speed_in_hours) as sum_network_speed_in_hours,sum(fm_dwell_time_in_hours) as sum_fm_dwell_time_in_hours, sum(total_trip_time_in_hours) as sum_total_trip_time_in_hours, sum(network_speed_in_hours)/count(distinct wbn) as avg_network_speed, 
  sum(fm_dwell_time_in_hours)/count(distinct wbn) as fm_dwell_time_avg_speed, sum(total_trip_time_in_hours)/count(distinct wbn) as total_avg_trip_time_,
  sum(sum_intransit_dwell_in_hour)/count(distinct wbn) as intransit_center_avg_dwell
  from
  
  (

select * from
 (    
select wbn, origin_facility_name, consignee_facility_name, bzn, trip_uuid_array, route_id_array, date(pickup_date) as pickup_date, intransit_centers_and_dwell_in_hour,
-- month(pickup_date) AS month_number, (week_of_year(pickup_date) - week_of_year(date_trunc('month', pickup_date)) + 1) AS week_of_month,
wbn_jounrney_path, first_pending_date, fm_last_scan_time,
cast(date_diff('minute', pickup_date, first_pending_date)/60.00 as double) as network_speed_in_hours,
cast(date_diff('minute', pickup_date, fm_last_scan_time)/60.00 as double) as fm_dwell_time_in_hours,
total_trip_time as total_trip_time_in_hours, sum_intransit_dwell_in_hour
from
(
select distinct a.wbn, a.origin_facility_name, a.consignee_facility_name, a.bzn, pickup_date, array_join(d.wbn_jounrney_path_t,',') as wbn_jounrney_path, first_pending_date, fm_last_scan_time, total_trip_time, trip_uuid_array, route_id_array,
-- array_join(trip_uuid_array, ',') as trip_uuid_array, array_join(route_id_array, ',') as route_id_array,  
e.sum_intransit_dwell_in_hour, array_join(f.intransit_centers_and_dwell_in_hour,',') as intransit_centers_and_dwell_in_hour
from wbn_journey a
left join fm_last_scan_time_df b on a.wbn = b.wbn
left join trips_fms_2 c on a.wbn = c.wbn
left join wbn_journey_top_path d on a.bzn = d.bzn_t and a.origin_facility_name = d.origin_facility_name_t and a.consignee_facility_name = d.consignee_facility_name_t
left join wbn_intransit_centers_dwell e on a.wbn = e.wbn
left join od_intransit_centers_dwell f on a.bzn = f.bzn_i and a.origin_facility_name = f.origin_facility_name_i and a.consignee_facility_name = f.consignee_facility_name_i
where first_pending_date is not null and fm_last_scan_time is not null
)
)
 where (network_speed_in_hours - fm_dwell_time_in_hours - total_trip_time_in_hours) > sum_intransit_dwell_in_hour
)
where (origin_facility_name is not null or consignee_facility_name is not null)
group by 1,2,3,4,5
having count(distinct wbn) > 20
order by 8 desc

 '''

In [0]:
cur = conn.cursor()
cur.execute(wbn_jrny_query)
columns = [desc[0] for desc in cur.description]
data = cur.fetchall()
wbn_jounery_df = pd.DataFrame(data, columns=columns)
cur.close()
conn.close()

In [0]:
wbn_jounery_df['route_id_array2'] = wbn_jounery_df['route_id_array'].apply(lambda x: list(set([item for sublist in x for item in sublist])) )
wbn_jounery_df['trip_id_array2'] = wbn_jounery_df['trip_uuid_array'].apply(lambda x: list(set([item for sublist in x for item in sublist])) )
wbn_jounery_df = wbn_jounery_df.drop(['route_id_array','trip_uuid_array'], axis=1)

wbn_jounery_df_spark = spark.createDataFrame(wbn_jounery_df)

In [0]:
print(wbn_jounery_df_spark.count())
# display(wbn_jounery_df_spark.filter((col('origin_facility_name')=='Surat_Kacholi_GW')& (col('consignee_facility_name')=='Vita_Adarshnagar_D')))
	

39302


In [0]:
# display(wbn_jounery_df_spark.filter((col('bzn').isin('A')) & (col('wbn_jounrney_path').contains('Bangalore_Peenya_I'))))

# & (col('origin_facility_name')=='Faridabad_MathuraRoad_GW')

In [0]:
wbn_ab_jounery_df_spark = wbn_jounery_df_spark.filter((col('bzn').isin('A','B')))

# Zone Average
grouped_df_ab = wbn_ab_jounery_df_spark.groupby("bzn").agg(sum("wbn_count").alias("zone_wbn_count"), sum("sum_network_speed_in_hours").alias("sum_network_speed_in_hours"), sum("sum_fm_dwell_time_in_hours").alias("sum_fm_dwell_time_in_hours"), sum("sum_total_trip_time_in_hours").alias("sum_total_trip_time_in_hours")).withColumn("zone_avg_network_speed", col("sum_network_speed_in_hours")/col("zone_wbn_count")).withColumn("zone_avg_fm_dwell", col("sum_fm_dwell_time_in_hours")/col("zone_wbn_count")).withColumn("zone_avg_trip_time", col("sum_total_trip_time_in_hours")/col("zone_wbn_count")).orderBy("bzn")

ab_zone_distances_avg_speed = grouped_df_ab.withColumnRenamed('bzn','zone').withColumnRenamed('distance_range','zone_distance').select("zone","zone_wbn_count", "zone_avg_network_speed","zone_avg_fm_dwell","zone_avg_trip_time")

display(ab_zone_distances_avg_speed)

zone zone_wbn_count zone_avg_network_speed zone_avg_fm_dwell zone_avg_trip_time A 139434 25.132273835649848 9.482169270048912 3.0430618924838573 B 977752 56.48131726654609 10.919128623618242 13.939945354127442

In [0]:
zone_ab_od_pairs = wbn_ab_jounery_df_spark.groupby("bzn","origin_facility_name","consignee_facility_name","wbn_jounrney_path", "route_id_array2","intransit_centers_and_dwell_in_hour").agg(sum("wbn_count").alias("wbn_count"), sum("sum_network_speed_in_hours").alias("sum_network_speed_in_hours"), sum("sum_fm_dwell_time_in_hours").alias("sum_fm_dwell_time_in_hours"), sum("sum_total_trip_time_in_hours").alias("sum_total_trip_time_in_hours"), sum("intransit_center_avg_dwell").alias("intransit_center_avg_dwell")).withColumn("avg_network_speed", col("sum_network_speed_in_hours")/col("wbn_count")).withColumn("avg_fm_dwell", col("sum_fm_dwell_time_in_hours")/col("wbn_count")).withColumn("avg_trip_time", col("sum_total_trip_time_in_hours")/col("wbn_count")) 

zone_ab_od_pairs_zone_avg = zone_ab_od_pairs.join(ab_zone_distances_avg_speed, (zone_ab_od_pairs['bzn'] == ab_zone_distances_avg_speed['zone']), 'left').drop('zone')

In [0]:
# All slower speed Cohorts 
Zone_AB_slower_cohort = zone_ab_od_pairs_zone_avg.drop('trip_id_array2').filter((col('avg_network_speed')>= col('zone_avg_network_speed')*1.2) & (col('wbn_count') >= 250)).orderBy(col('bzn'),col('wbn_count').desc())
display(Zone_AB_slower_cohort)

bzn origin_facility_name consignee_facility_name wbn_jounrney_path route_id_array2 intransit_centers_and_dwell_in_hour wbn_count sum_network_speed_in_hours sum_fm_dwell_time_in_hours sum_total_trip_time_in_hours intransit_center_avg_dwell avg_network_speed avg_fm_dwell avg_trip_time zone_wbn_count zone_avg_network_speed zone_avg_fm_dwell zone_avg_trip_time A Bhiwandi_Lonad_GW Mumbai_Khardipada_D Bhiwandi_Lonad_GW (Maharashtra) -> Mumbai_Patlipada_I (Maharashtra) -> Mumbai_Khardipada_D (Maharashtra) List(thanos::sroute:a1b45295-8182-42a8-8832-e8edf293a231, thanos::sroute:fad212c5-5c6d-45fb-bc17-052ef0d3bc78, thanos::sroute:db58d00b-646a-403a-8985-73f7f7e07096, thanos::sroute:cc0665af-48b4-4db1-aa05-8aa58905b94a, thanos::sroute:3fb52c2c-0e0f-4379-9d47-e281dbf09dc1, thanos::sroute:9aaa1832-9ab1-4353-8afd-4feefc4d9a43) Mumbai_Patlipada_I (Maharashtra) - (3.94 hours) ,Mumbai_MahapeMIDC_L (Maharashtra) - (31.83 hours) 980 30130.700000000004 11557.900000000009 3721.9236111135056 3.9303979591836455 30.745612244897963 11.79377551020409 3.7978812358301077 139434 25.132273835649848 9.482169270048912 3.0430618924838573 A Bhiwandi_Lonad_GW Mumbai_AndheriWest_D Bhiwandi_Lonad_GW (Maharashtra) -> Mumbai_Jogeshwri_I (Maharashtra) -> Mumbai_AndheriWest_D (Maharashtra) List(thanos::sroute:787573bd-6a27-4cd5-9ea5-2d2b0c7cd541, thanos::sroute:1a4c40ef-6a67-4794-bfd1-0eba93883010, thanos::sroute:a720e97e-6e93-4c5b-b619-a983392d85c7, thanos::sroute:64254f11-5e3b-42c4-ae4a-168dde76cd24, thanos::sroute:4cbc4718-92f8-4baa-ae81-a2856805e008, thanos::sroute:0e1df239-9574-48a7-afdc-1629902d8cc5, thanos::sroute:1245cb8a-cb90-43cc-9fea-e029b95d7c80, thanos::sroute:5b3338f5-6218-4bd2-b82e-62af3e701602, thanos::sroute:8c91a96e-b67a-4946-bd5d-846b50f8a0d9, thanos::sroute:6b9884dd-9310-4971-9a12-fef44a5994de, thanos::sroute:67e2aad2-6342-410b-83a2-e38c254112f4) Mumbai_Jogeshwri_I (Maharashtra) - (8.08 hours) ,Mumbai_Mograpada_D (Maharashtra) - (24.90 hours) 732 23790.090000000026 9762.11000000001 3594.862444450267 8.081243169398922 32.50012295081971 13.336215846994548 4.911014268374681 139434 25.132273835649848 9.482169270048912 3.0430618924838573 A Bhiwandi_Lonad_GW Mumbai_Charkop_D Bhiwandi_Lonad_GW (Maharashtra) -> Mumbai_Mirabhayandar_I (Maharashtra) -> Mumbai_Charkop_D (Maharashtra) List(thanos::sroute:9c5daba8-2834-4b1c-b217-2e0eace010fd, thanos::sroute:71cb579f-3720-41c7-af7c-0378569cdba4, thanos::sroute:f270f064-8ef3-4811-9b15-24cfc4896055, thanos::sroute:9ea30e76-0a79-45da-8f64-82af598a62b0, thanos::sroute:f4a2df79-8b30-4bff-8ce1-c2af71891638, thanos::sroute:3e0acbf9-ad8d-4d92-8c36-43fd0f05733d, thanos::sroute:87400678-d232-425a-b79b-898c53274917, thanos::sroute:e50c8332-4ba2-4d35-8b9f-bb690f8ff762, thanos::sroute:2836074e-3d1d-4e6f-a4a1-b2645d8b5a25, thanos::sroute:140e40b6-9a12-4a7b-bef4-b09ec501c138, thanos::sroute:936a9459-c57c-48e4-b989-5e5d1351809b, thanos::sroute:9fa220ac-0e47-4265-920b-cae093edacd5, thanos::sroute:84649477-f911-4768-a455-221822894fdc, thanos::sroute:398b9eab-0cfe-4697-b293-c8348944bb03, thanos::sroute:835704ae-6855-49fd-ba4b-64f91edbc799, thanos::sroute:d9d386c8-8582-4d7b-bb16-5721162fad47, thanos::sroute:20dcc3d7-3146-447a-a05f-c2d3e506a26b) Mumbai_Mirabhayandar_I (Maharashtra) - (5.16 hours) 690 23526.460000000003 9355.149999999998 2902.2087222118453 5.153724637681158 34.09631884057971 13.558188405797098 4.206099597408471 139434 25.132273835649848 9.482169270048912 3.0430618924838573 A Bhiwandi_Lonad_GW Mumbai_VashiWard_D Bhiwandi_Lonad_GW (Maharashtra) -> Mumbai_MahapeMIDC2_I (Maharashtra) -> Mumbai_VashiWard_D (Maharashtra) List(thanos::sroute:41a91333-83da-4cc0-89e4-600ee6853100, thanos::sroute:f354f850-be29-47cc-bd61-153c232b62e6, thanos::sroute:ac1462fb-c340-4fae-a39e-89173d34ac80, thanos::sroute:5afdad2b-e1b1-4743-bc21-82cba53ec4cb, thanos::sroute:9131d77d-8990-4e50-9900-6f76d45f473e, thanos::sroute:043669a8-90ce-4781-8af2-d658edc2174f, thanos::sroute:686e8db1-3ee5-4e6b-97d7-3ace67f51fd5, thanos::sroute:c7fef7bd-8d7e-4

In [0]:
# # Customized cohorts (Filtered on condition)

# display(wbn_jounery_df_spark.filter((col('bzn')== 'B') & (col('origin_facility_name') == 'Noida_Bairangpur_GW') & (col('consignee_facility_name').isin(''))).groupby("bzn","origin_facility_name").agg(sum("wbn_count").alias("wbn_count"), sum("sum_network_speed_in_hours").alias("sum_network_speed_in_hours"), sum("sum_fm_dwell_time_in_hours").alias("sum_fm_dwell_time_in_hours"), sum("sum_total_trip_time_in_hours").alias("sum_total_trip_time_in_hours")).withColumn("avg_network_speed", col("sum_network_speed_in_hours")/col("wbn_count")).withColumn("avg_fm_dwell", col("sum_fm_dwell_time_in_hours")/col("wbn_count")).withColumn("avg_trip_time", col("sum_total_trip_time_in_hours")/col("wbn_count")))


# # & (col('origin_facility_name') == 'Delhi_Airport_GW') & (col('consignee_facility_name').isin('Mohali_Sector123_D'))))

In [0]:
wbn_cd_agg_jounery_df_spark = wbn_jounery_df_spark.filter((col('bzn').isin('C','D')))

# Zone Average
grouped_df_cd = wbn_cd_agg_jounery_df_spark.groupby("bzn").agg(sum("wbn_count").alias("zone_wbn_count"), sum("sum_network_speed_in_hours").alias("sum_network_speed_in_hours"), sum("sum_fm_dwell_time_in_hours").alias("sum_fm_dwell_time_in_hours"), sum("sum_total_trip_time_in_hours").alias("sum_total_trip_time_in_hours")).withColumn("zone_avg_network_speed", col("sum_network_speed_in_hours")/col("zone_wbn_count")).withColumn("zone_avg_fm_dwell", col("sum_fm_dwell_time_in_hours")/col("zone_wbn_count")).withColumn("zone_avg_trip_time", col("sum_total_trip_time_in_hours")/col("zone_wbn_count")).orderBy("bzn")

# display(grouped_df_ab)

cd_zone_distances_avg_speed = grouped_df_cd.withColumnRenamed('bzn','zone').withColumnRenamed('distance_range','zone_distance').select("zone", "zone_wbn_count", "zone_avg_network_speed","zone_avg_fm_dwell","zone_avg_trip_time")
display(cd_zone_distances_avg_speed)

zone zone_wbn_count zone_avg_network_speed zone_avg_fm_dwell zone_avg_trip_time C 237543 80.5265660533041 13.03934352938204 37.547587372718 D 2242695 90.74123186166631 6.639936821547271 38.16493285815058

In [0]:
zone_cd_od_pair_all = spark.read.parquet('/dbfs/FileStore/network_speed/zone_cd_od_pairs_distances_till_sunday.parquet')

zone_cd_od_pair_all = zone_cd_od_pair_all.withColumnRenamed('origin_facility_name','origin_facility').withColumnRenamed('consignee_facility_name','consignee_facility').select('origin_facility','consignee_facility','distance_km').dropDuplicates()
# print(zone_cd_od_pair_all.count())

In [0]:
# display(zone_cd_od_pair_all)

In [0]:
wbn_cd_jounery_df_spark = wbn_jounery_df_spark.filter((col('bzn').isin('C','D') &(col('wbn_count') >= 10)))

zone_cd_wbn_journey_distance = wbn_cd_jounery_df_spark.join(zone_cd_od_pair_all, (wbn_cd_jounery_df_spark['origin_facility_name'] == zone_cd_od_pair_all['origin_facility']) & (wbn_cd_jounery_df_spark['consignee_facility_name'] == zone_cd_od_pair_all['consignee_facility']), 'left').drop('origin_facility', 'consignee_facility')

In [0]:
wbn_cd_jounery_df_spark.count()

29994

In [0]:
zone_cd_wbn_journey_distance = zone_cd_wbn_journey_distance.withColumn( "distance_range",
    when((col("distance_km") < 800), "a.0-800 km")
    .when((col("distance_km") >= 800) & (col("distance_km") < 1100), "b.800-1100 km")
    .when((col("distance_km") >= 1100) & (col("distance_km") < 1400), "c.1100-1400 km")
    .when((col("distance_km") >= 1400), "d.1400+ km"))

In [0]:
display(zone_cd_wbn_journey_distance.filter(col('distance_range').isNull()).count())

1839

In [0]:
grouped_df = zone_cd_wbn_journey_distance.groupby("bzn", "distance_range").agg(sum("wbn_count").alias("wbn_count"), sum("sum_network_speed_in_hours").alias("sum_network_speed_in_hours"), sum("sum_fm_dwell_time_in_hours").alias("sum_fm_dwell_time_in_hours"), sum("sum_total_trip_time_in_hours").alias("sum_total_trip_time_in_hours")).withColumn("zone_avg_network_speed", col("sum_network_speed_in_hours")/col("wbn_count")).withColumn("zone_avg_fm_dwell", col("sum_fm_dwell_time_in_hours")/col("wbn_count")).withColumn("zone_avg_trip_time", col("sum_total_trip_time_in_hours")/col("wbn_count")).orderBy("bzn", "distance_range")

# display(grouped_df.filter(col('distance_range').isNotNull()))

cd_zone_distances_avg_speed = grouped_df.filter(col('distance_range').isNotNull()).withColumnRenamed('bzn','zone').withColumnRenamed('distance_range','zone_distance').select("zone", "zone_distance", "zone_avg_network_speed","zone_avg_fm_dwell","zone_avg_trip_time")
display(cd_zone_distances_avg_speed)

zone zone_distance zone_avg_network_speed zone_avg_fm_dwell zone_avg_trip_time C a.0-800 km 74.33742680972956 14.722818857115115 23.782752565769606 C b.800-1100 km 72.84388360128621 14.088598499464094 31.008845329874774 C c.1100-1400 km 77.83392557556978 11.596224064338568 38.259483719884265 C d.1400+ km 88.97255152097821 12.814929744120693 47.10451888109819 D a.0-800 km 74.07915553830684 9.790929086789879 23.558713008022355 D b.800-1100 km 85.02580743416051 4.761875009687972 33.35789495625118 D c.1100-1400 km 88.77056784546933 5.308460537812166 38.45353463094062 D d.1400+ km 107.85828560784435 7.3195866060355685 51.04895134242544

In [0]:
# "bzn","origin_facility_name","consignee_facility_name", "distance_range"

grouped_df_2 = zone_cd_wbn_journey_distance.groupby("bzn","origin_facility_name","consignee_facility_name","distance_km", "distance_range","wbn_jounrney_path","route_id_array2","intransit_centers_and_dwell_in_hour").agg(sum("wbn_count").alias("wbn_count"), sum("sum_network_speed_in_hours").alias("sum_network_speed_in_hours"), sum("sum_fm_dwell_time_in_hours").alias("sum_fm_dwell_time_in_hours"), sum("sum_total_trip_time_in_hours").alias("sum_total_trip_time_in_hours"), sum("intransit_center_avg_dwell").alias("intransit_center_avg_dwell")).withColumn("avg_network_speed", col("sum_network_speed_in_hours")/col("wbn_count")).withColumn("avg_fm_dwell", col("sum_fm_dwell_time_in_hours")/col("wbn_count")).withColumn("avg_trip_time", col("sum_total_trip_time_in_hours")/col("wbn_count"))

grouped_df_2_with_zone_avg = grouped_df_2.join(cd_zone_distances_avg_speed, (grouped_df_2['bzn'] == cd_zone_distances_avg_speed['zone']) & (grouped_df_2['distance_range'] == cd_zone_distances_avg_speed['zone_distance']), 'left').drop('zone_distance', 'zone')


In [0]:
# all cohorts with slower network speed

Zone_CD_slower_cohort = grouped_df_2_with_zone_avg.filter((col('avg_network_speed') >= col('zone_avg_network_speed')*1.1) & (col('wbn_count') >= 200)).orderBy(col('bzn'),col('wbn_count').desc())

display(Zone_CD_slower_cohort)

# display(grouped_df_2_with_zone_avg.filter((col('bzn')== 'C') & (col('origin_facility_name') == 'Delhi_Airport_GW')).orderBy(col('distance_range')).select('bzn','origin_facility_name','wbn_jounrney_path','distance_range','wbn_count','avg_network_speed','Avg_fm_dwell','Avg_trip_time'))

# display(grouped_df_2_with_zone_avg)

bzn origin_facility_name consignee_facility_name distance_km distance_range wbn_jounrney_path route_id_array2 intransit_centers_and_dwell_in_hour wbn_count sum_network_speed_in_hours sum_fm_dwell_time_in_hours sum_total_trip_time_in_hours intransit_center_avg_dwell avg_network_speed avg_fm_dwell avg_trip_time zone_avg_network_speed zone_avg_fm_dwell zone_avg_trip_time C Bhiwandi_Lonad_GW Hyderabad_Rajarajeshwari_D 687.2099000000001 a.0-800 km Bhiwandi_Lonad_GW (Maharashtra) -> Hyderabad_Medchal_GW (Telangana) -> Hyderabad_Rajarajeshwari_D (Telangana) List(thanos::sroute:361a7169-48bf-49ac-9bd4-c72b1243d3ad, thanos::sroute:75697e09-38b8-423c-8338-53983bf891ae, thanos::sroute:ef91f9ce-2b4d-4264-a492-5e3510020259, thanos::sroute:351b10a0-6497-44bf-bfe7-52f1af91e87e, thanos::sroute:52d5edd3-1bcd-4f17-a63a-64511cec52ed, thanos::sroute:e48fa709-44d7-49a4-b988-9aa564e61b41, thanos::sroute:1b5e025f-79bd-43e2-ba54-ff0d48a60d73, thanos::sroute:3a8f1458-7124-43b3-9c49-b7a8aff89d2c, thanos::sroute:d4ebed1e-7c43-4dce-a293-719b8cef189d, thanos::sroute:b2e5cbf5-918a-42f8-872f-3354cce0397d, thanos::sroute:eb0f69c0-6ce2-4e6f-b141-c34042e3fc90, thanos::sroute:8727f229-f9cc-4ec0-86f3-7eb0095bcef8, thanos::sroute:b6c6ef9d-de9b-4468-bd9a-643f41b7cb34, thanos::sroute:8f8e7f3e-ebcb-42a6-9188-0a8f1adcf561, thanos::sroute:f904dbe1-aa5b-4490-9dd5-8717a152a5a0, thanos::sroute:76c64f58-4da7-4166-8bb2-e0a92dfed720, thanos::sroute:17a3c97c-9d44-49d1-8386-bb1859e07f1d, thanos::sroute:b940e625-90e2-44ed-a765-27385722b98b, thanos::sroute:a32d4d20-0301-4c44-8505-51229502e0c9, thanos::sroute:5433fe98-1b9e-4891-bc22-ba45b00cdf05, thanos::sroute:b70cda78-00da-495c-99b0-8b10bf8086f2) Hyderabad_Medchal_GW (Telangana) - (40.42 hours) 450 39510.689999999995 6547.749999999998 14231.65980555658 40.416444444444366 87.80153333333332 14.550555555555551 31.62591067901462 74.33742680972956 14.722818857115115 23.782752565769606 C Bhiwandi_Lonad_GW Hyderabad_KTRColony_D 691.2028 a.0-800 km Bhiwandi_Lonad_GW (Maharashtra) -> Hyderabad_Medchal_GW (Telangana) -> Hyderabad_KTRColony_D (Telangana) List(thanos::sroute:ce2107f0-84b2-483e-80f4-69096ff7c9be, thanos::sroute:ef91f9ce-2b4d-4264-a492-5e3510020259, thanos::sroute:351b10a0-6497-44bf-bfe7-52f1af91e87e, thanos::sroute:52d5edd3-1bcd-4f17-a63a-64511cec52ed, thanos::sroute:1b5e025f-79bd-43e2-ba54-ff0d48a60d73, thanos::sroute:3a8f1458-7124-43b3-9c49-b7a8aff89d2c, thanos::sroute:d4ebed1e-7c43-4dce-a293-719b8cef189d, thanos::sroute:b2e5cbf5-918a-42f8-872f-3354cce0397d, thanos::sroute:eb0f69c0-6ce2-4e6f-b141-c34042e3fc90, thanos::sroute:b6c6ef9d-de9b-4468-bd9a-643f41b7cb34, thanos::sroute:8f8e7f3e-ebcb-42a6-9188-0a8f1adcf561, thanos::sroute:344907ff-7792-41f4-9f32-385be726aa59, thanos::sroute:235f9a1f-7b9c-406d-99a0-e4410cb28931, thanos::sroute:243ac93b-45bb-416d-aa4b-3f592dbdc7ca, thanos::sroute:4b519a88-80ea-4a35-8221-933a5bbf8db7, thanos::sroute:76c64f58-4da7-4166-8bb2-e0a92dfed720, thanos::sroute:35252a8e-6996-4124-b4e4-2aaf6e086d59, thanos::sroute:a32d4d20-0301-4c44-8505-51229502e0c9, thanos::sroute:5433fe98-1b9e-4891-bc22-ba45b00cdf05, thanos::sroute:b70cda78-00da-495c-99b0-8b10bf8086f2) Hyderabad_Medchal_GW (Telangana) - (40.17 hours) 432 37163.41000000002 6327.549999999997 12576.602583333604 40.18659722222216 86.02641203703708 14.647106481481476 29.1125059799389 74.33742680972956 14.722818857115115 23.782752565769606 C Bhiwandi_Lonad_GW Ahmedabad_Pravinnagar_D 503.3014 a.0-800 km Bhiwandi_Lonad_GW (Maharashtra) -> Ahmedabad_Kanera_GW (Gujarat) -> Ahmedabad_Pravinnagar_D (Gujarat) List(thanos::sroute:fdbeafb9-90cb-4d9c-a1f2-f0e1e3742937, thanos::sroute:6d89c102-6691-4700-8842-cdb85c2da21b, thanos::sroute:67bb1f2c-83ef-4c38-aa2c-863860ff134c, thanos::sroute:aca1b7b1-6246-40d1-b94a-d1e7b60ffaf3, thanos::sroute:5490ff26-7c10-40b3-b1b7-4bd1c1a90049, thanos::sroute:496786ca-fb47-4e11-8542-a8e4bdcddff0, thanos::sroute:3467e4f2-dc03-45f4-acdb-b6fd29f0485b) Ahmedabad_Kanera_GW (Gujarat) - (41.43 hours) ,Ahmedabad_Vejalpur_D (Gujarat)

In [0]:
# zone_ab_s3_path = "s3://abis3/Sheetal/Network_speed_cohorts/Zone_AB_slower_cohorts_" + str(current_date) 

# zone_cd_s3_path = "s3://abis3/Sheetal/Network_speed_cohorts/Zone_CD_slower_cohorts_" + str(current_date) 

zone_ab_s3_path = "s3://abis3/Sheetal/Network_speed_cohorts/Zone_AB_slower_cohorts_12_18_may"

zone_cd_s3_path = "s3://abis3/Sheetal/Network_speed_cohorts/Zone_CD_slower_cohorts_12_18_may"


print(zone_ab_s3_path)
print(zone_cd_s3_path)

Zone_AB_slower_cohort.write.mode('overwrite').parquet(zone_ab_s3_path)
Zone_CD_slower_cohort.write.mode('overwrite').parquet(zone_cd_s3_path)

s3://abis3/Sheetal/Network_speed_cohorts/Zone_AB_slower_cohorts_12_18_may
s3://abis3/Sheetal/Network_speed_cohorts/Zone_CD_slower_cohorts_12_18_may


In [0]:
# s3://abis3/Sheetal/Network_speed_cohorts/Zone_AB_slower_cohorts_21_27_april
# s3://abis3/Sheetal/Network_speed_cohorts/Zone_CD_slower_cohorts_21_27_april

# s3://abis3/Sheetal/Network_speed_cohorts/Zone_AB_slower_cohorts_28_04_may
# s3://abis3/Sheetal/Network_speed_cohorts/Zone_CD_slower_cohorts_28_04_may

# s3://abis3/Sheetal/Network_speed_cohorts/Zone_AB_slower_cohorts_05_11_may
# s3://abis3/Sheetal/Network_speed_cohorts/Zone_CD_slower_cohorts_05_11_may

# s3://abis3/Sheetal/Network_speed_cohorts/Zone_AB_slower_cohorts_12_18_may
# s3://abis3/Sheetal/Network_speed_cohorts/Zone_CD_slower_cohorts_12_18_may



In [0]:
zone_ab_s3_path = "s3://abis3/Sheetal/Network_speed_cohorts/Zone_AB_slower_cohorts_21_27_april"

zone_cd_s3_path = "s3://abis3/Sheetal/Network_speed_cohorts/Zone_CD_slower_cohorts_21_27_april"

print(zone_ab_s3_path)
print(zone_cd_s3_path)

s3://abis3/Sheetal/Network_speed_cohorts/Zone_AB_slower_cohorts_21_27_april
s3://abis3/Sheetal/Network_speed_cohorts/Zone_CD_slower_cohorts_21_27_april


In [0]:
Zone_AB_slower_cohort = spark.read.parquet(zone_ab_s3_path)
Zone_CD_slower_cohort = spark.read.parquet(zone_cd_s3_path)

Zone_CD_slower_cohort2 = Zone_CD_slower_cohort.drop('distance_km',	'distance_range')
Zone_AB_slower_cohort2 = Zone_AB_slower_cohort.drop('zone_wbn_count')
all_zone_slower_cohorts = Zone_AB_slower_cohort2.union(Zone_CD_slower_cohort2)
all_zone_slower_cohorts = all_zone_slower_cohorts.withColumn('avg_mm_dwell', col('avg_network_speed')-col('avg_fm_dwell')-col('avg_trip_time')).withColumn('zone_mm_dwell', col('zone_avg_network_speed')-col('zone_avg_fm_dwell')-col('zone_avg_trip_time')).select('bzn',
 'origin_facility_name',
 'consignee_facility_name',
 'wbn_jounrney_path',
 'route_id_array2',
 'intransit_centers_and_dwell_in_hour',
 'wbn_count',
 'sum_network_speed_in_hours',
 'sum_fm_dwell_time_in_hours',
 'sum_total_trip_time_in_hours',
 'avg_network_speed',
 'avg_fm_dwell',
 'avg_trip_time',
 'avg_mm_dwell',
 'intransit_center_avg_dwell',
 'zone_avg_network_speed',
 'zone_avg_fm_dwell',
 'zone_avg_trip_time',
 'zone_mm_dwell')

print(all_zone_slower_cohorts.count() == Zone_AB_slower_cohort.count() + Zone_CD_slower_cohort2.count())

True


In [0]:
all_zone_slower_cohorts_21_27_april = all_zone_slower_cohorts
# all_zone_slower_cohorts_28_04_may = all_zone_slower_cohorts

# all_zone_slower_cohorts_05_11_may = all_zone_slower_cohorts
# all_zone_slower_cohorts_12_18_may = all_zone_slower_cohorts

In [0]:

print(all_zone_slower_cohorts_21_27_april.count())
print(all_zone_slower_cohorts_28_04_may.count())

print(all_zone_slower_cohorts_05_11_may.count())
print(all_zone_slower_cohorts_12_18_may.count())

414
225
754
538


In [0]:
# Keep Latest week as first table
join1 = all_zone_slower_cohorts_12_18_may.alias('all_zone_slower_cohorts_12_18_may').join(all_zone_slower_cohorts_05_11_may.alias('all_zone_slower_cohorts_05_11_may'), on  = ['bzn','origin_facility_name','consignee_facility_name'], how = 'inner')
join2 = join1.join(all_zone_slower_cohorts_28_04_may.alias('all_zone_slower_cohorts_28_04_may'), on  = ['bzn','origin_facility_name','consignee_facility_name'], how = 'inner')
join3 = join2.join(all_zone_slower_cohorts_21_27_april.alias('all_zone_slower_cohorts_21_27_april'), on  = ['bzn','origin_facility_name','consignee_facility_name'], how = 'inner')

In [0]:
display(join3)

bzn origin_facility_name consignee_facility_name wbn_jounrney_path route_id_array2 intransit_centers_and_dwell_in_hour wbn_count sum_network_speed_in_hours sum_fm_dwell_time_in_hours sum_total_trip_time_in_hours avg_network_speed avg_fm_dwell avg_trip_time avg_mm_dwell intransit_center_avg_dwell zone_avg_network_speed zone_avg_fm_dwell zone_avg_trip_time zone_mm_dwell wbn_jounrney_path route_id_array2 intransit_centers_and_dwell_in_hour wbn_count sum_network_speed_in_hours sum_fm_dwell_time_in_hours sum_total_trip_time_in_hours avg_network_speed avg_fm_dwell avg_trip_time avg_mm_dwell intransit_center_avg_dwell zone_avg_network_speed zone_avg_fm_dwell zone_avg_trip_time zone_mm_dwell wbn_jounrney_path route_id_array2 intransit_centers_and_dwell_in_hour wbn_count sum_network_speed_in_hours sum_fm_dwell_time_in_hours sum_total_trip_time_in_hours avg_network_speed avg_fm_dwell avg_trip_time avg_mm_dwell intransit_center_avg_dwell zone_avg_network_speed zone_avg_fm_dwell zone_avg_trip_time zone_mm_dwell wbn_jounrney_path route_id_array2 intransit_centers_and_dwell_in_hour wbn_count sum_network_speed_in_hours sum_fm_dwell_time_in_hours sum_total_trip_time_in_hours avg_network_speed avg_fm_dwell avg_trip_time avg_mm_dwell intransit_center_avg_dwell zone_avg_network_speed zone_avg_fm_dwell zone_avg_trip_time zone_mm_dwell A Hyderabad_Medchal_GW Shankarpalle_Bilalcolony_D Hyderabad_Medchal_GW (Telangana) -> Hyderabad_Shamshbd_H (Telangana) -> Shankarpalle_Bilalcolony_D (Telangana) List(thanos::sroute:46b5af4c-ace4-4a1f-a8aa-5d2a0186d560, thanos::sroute:ce68b594-45f2-40b8-95dc-94734bc8da1d, thanos::sroute:5e185360-5561-40a2-b285-0089a72e0e5b, thanos::sroute:f02497d6-3a40-4b00-bd2f-53048c0f64b1, thanos::sroute:0b4fc37b-503e-4a03-93e2-c0a0cd871297, thanos::sroute:bd1a5f04-b9bb-4433-bf40-46d87e80ae07, thanos::sroute:f49f962a-cb7d-44c1-a67e-2f9c4ca034d7, thanos::sroute:ae58b629-4f15-4ab9-a6c0-01fb4965e177, thanos::sroute:c6a4ef87-8d7c-4014-a54f-724ca25acd36, thanos::sroute:df17ef1a-0281-4749-82ea-aa53a13d15eb, thanos::sroute:21b41644-90ab-4267-9aa2-f7c3ebff27ec, thanos::sroute:0a5440fc-fbb4-4214-ba89-3a2b8be1216c, thanos::sroute:59ab0d09-28ed-4475-a5ea-da5cda22deff, thanos::sroute:c5b9114d-a5ea-46ef-a697-6f39e64b1c7c, thanos::sroute:d784c597-5d8f-4f7d-832d-d45b427b3729, thanos::sroute:28fc7f52-ee57-47c2-8d9f-c7afc216e456, thanos::sroute:c51aa66a-b200-4845-90c7-63d9a1198d5a, thanos::sroute:0d714d9e-f5c9-4aa8-9fe4-d6cce4c80ef9, thanos::sroute:e3d2a8fa-def7-4acc-b483-e93a4cbd7586, thanos::sroute:4ea9a8de-bb75-4a91-9aea-fa5166741a60, thanos::sroute:2ae4a09c-c3ee-430c-b316-45f461eccd74, thanos::sroute:23f8e864-bb80-440b-aa8f-1c1c262d5613, thanos::sroute:e186287a-246c-4263-9822-c46b41a1840c, thanos::sroute:358bca40-c8ce-446e-b38f-900c6a45cc64, thanos::sroute:fda00390-c449-4a4a-9fd2-ca0a6072f5c2, thanos::sroute:fdc4913e-19bd-4674-92c9-05dd3382cf0f, thanos::sroute:a46e2fae-d305-4e68-8ab3-9f712c6c7ce6) Hyderabad_Shamshbd_H (Telangana) - (18.05 hours) 468 18072.470000000005 6428.470000000004 2025.0241666701093 38.6163888888889 13.736047008547017 4.326974715107071 20.55336716523481 18.044615384615394 25.132273835649848 9.482169270048912 3.0430618924838573 12.607042673117078 Hyderabad_Medchal_GW (Telangana) -> Hyderabad_Shamshbd_H (Telangana) -> Shankarpalle_Bilalcolony_D (Telangana) List(thanos::sroute:46b5af4c-ace4-4a1f-a8aa-5d2a0186d560, thanos::sroute:5e185360-5561-40a2-b285-0089a72e0e5b, thanos::sroute:900c2660-100d-4ed1-9963-a0cc3199f6b0, thanos::sroute:0b4fc37b-503e-4a03-93e2-c0a0cd871297, thanos::sroute:763d0b2b-3542-4d9e-a7d0-df26b97316d3, thanos::sroute:76ed9296-e88e-4282-a60d-44026f6612b5, thanos::sroute:52e485a5-ec63-4f70-869b-90e38fa74f96, thanos::sroute:80afb947-12c8-4b5b-8362-0971dd59ab95, thanos::sroute:0981af35-da79-451d-ac5e-f3801e625c87, thanos::sroute:21b41644-90ab-4267-9aa2-f7c3ebff27ec, thanos::sroute:0bc102ef-a107-4869-823c-ae215e415881, thanos::sroute:0a5440fc-fbb4-4214-ba89-3a2b8be1216c, thanos::sroute:6454c27a-b744-4e84-be88-

In [0]:
last_week_zone_AB = spark.read.parquet('s3://abis3/Sheetal/Network_speed_cohorts/Zone_AB_slower_cohorts_2025-02-18')
last_week_zone_CD = spark.read.parquet('s3://abis3/Sheetal/Network_speed_cohorts/Zone_CD_slower_cohorts_2025-02-18')

last_week_zone_CD2 = last_week_zone_CD.drop('distance_km',	'distance_range')

last_week_all_zone_slower_cohorts = last_week_zone_AB.union(last_week_zone_CD2)

In [0]:
zone = 'D'
oc = 'Noida_Bairangpur_GW'

last_week_cohort_speed = last_week_all_zone_slower_cohorts.filter((col('bzn') == zone) & (col('origin_facility_name')== oc)).groupby("bzn", "origin_facility_name").agg(sum("wbn_count").alias("wbn_count"), sum("sum_network_speed_in_hours").alias("sum_network_speed_in_hours"), sum("sum_fm_dwell_time_in_hours").alias("sum_fm_dwell_time_in_hours"), sum("sum_total_trip_time_in_hours").alias("sum_total_trip_time_in_hours")).withColumn("zone_avg_network_speed", col("sum_network_speed_in_hours")/col("wbn_count")).withColumn("zone_avg_fm_dwell", col("sum_fm_dwell_time_in_hours")/col("wbn_count")).withColumn("zone_avg_trip_time", col("sum_total_trip_time_in_hours")/col("wbn_count")).orderBy("bzn", "origin_facility_name")

display(last_week_cohort_speed)

bzn origin_facility_name wbn_count sum_network_speed_in_hours sum_fm_dwell_time_in_hours sum_total_trip_time_in_hours zone_avg_network_speed zone_avg_fm_dwell zone_avg_trip_time D Noida_Bairangpur_GW 10690 932693.5299999999 134042.04 386321.5538332776 87.24916089803554 12.539012160898036 36.13859250077433

In [0]:
cn_list = last_week_all_zone_slower_cohorts.filter((col('bzn') == zone) & (col('origin_facility_name')== oc)).select('consignee_facility_name').distinct().rdd.flatMap(lambda x: x).collect()

print(len(cn_list))
print(cn_list)

display(wbn_jounery_df_spark.filter((col('bzn')== zone) & (col('origin_facility_name') == oc) & (col('consignee_facility_name').isin(cn_list))).groupby("bzn","origin_facility_name").agg(sum("wbn_count").alias("wbn_count"), sum("sum_network_speed_in_hours").alias("sum_network_speed_in_hours"), sum("sum_fm_dwell_time_in_hours").alias("sum_fm_dwell_time_in_hours"), sum("sum_total_trip_time_in_hours").alias("sum_total_trip_time_in_hours")).withColumn("avg_network_speed", col("sum_network_speed_in_hours")/col("wbn_count")).withColumn("avg_fm_dwell", col("sum_fm_dwell_time_in_hours")/col("wbn_count")).withColumn("avg_trip_time", col("sum_total_trip_time_in_hours")/col("wbn_count")))

32
['Keshkal_Surdongar_D', 'Gaya_Balajinagar_D', 'Udaipur_PratapNagar_D', 'Deo_DiwanBigha_D', 'Sasaram_Karwandiya_D', 'Bihta_Kateshwar_D', 'Jodhpur', 'Goa_Margao_D', 'Gaya_HanumanNagar1_D', 'Manda_BabhaniHethar_D', 'Varanasi', 'Gonda_Babhanikanoongo_D', 'Mundra_Umiyanagar_D', 'Koraon_AmbedkarNagar_D', 'Garhwa_Bishunpur_D', 'Bhilwara_RIICOIndArea_D', 'Varanasi_Sarnath_D', 'Goh_Golapar_D', 'Bilaspur_Lingiyadih_D', 'Bahadurganj_Pauakhali_D', 'Hassan_Vidyuthnagara_D', 'Pathalgaon_Kmkla_D', 'Kherwara_Banjaria_D', 'Goa_Porvorim_D', 'Ujjain_Rishinagar_D', 'Azamgarh_Kotwa_D', 'Jodhpur_Boranada_D', 'Mirzapur_Lalganj_D', 'Tirupati_RAgraharam_D', 'Lailunga_BanjariPara_D', 'Varanasi_Dhupchandi_D', 'Udaipur_Navlok_D']


bzn origin_facility_name wbn_count sum_network_speed_in_hours sum_fm_dwell_time_in_hours sum_total_trip_time_in_hours avg_network_speed avg_fm_dwell avg_trip_time D Noida_Bairangpur_GW 9018 726111.8999999999 102043.75999999998 295375.17361112026 80.51806387225548 11.31556442670215 32.753955822923075

### Extracting Connection Time for The OD Pairs route connection

In [0]:
zone = ['C']
origin = ['Faridabad_MathuraRoad_GW']
destination = ['Pune_Kalewadi_D']


# Zone_CD_slower_cohort all_zone_slower_cohorts_03_09_march
route_id_array = all_zone_slower_cohorts_17_23_march.filter((col('bzn').isin(zone)) & (col('origin_facility_name').isin(origin)) & (col('consignee_facility_name').isin(destination))).select('route_id_array2').collect()[0][0]

route_id_array_tup =  tuple(route_id_array)
route_id_array_tup

('thanos::sroute:26baa17f-5399-48e0-a0d3-df7779cbbd4a',
 'thanos::sroute:6b84b847-d4b5-4641-8f2e-5e1059fde47e',
 'thanos::sroute:38881dc7-8e3e-439d-9cbc-7f966596eabb',
 'thanos::sroute:76ec74f2-8d96-4952-85a2-e92231b2210c',
 'thanos::sroute:0afd6f8e-7486-47be-b206-4fdaab21f948',
 'thanos::sroute:4f9ba6d5-0879-4704-8f98-0cf786a5669c',
 'thanos::sroute:8d07a5ea-6d03-47fe-89cc-6b85ff65dba3',
 'thanos::sroute:99293255-3dc5-4938-8aef-e5de8c9668a9',
 'thanos::sroute:18d9b3b7-71fe-44d2-9258-4f7fd3b7742f',
 'thanos::sroute:c2432a9f-3cd7-430e-9b53-f2816c7f6225',
 'thanos::sroute:29fb5593-129c-4527-8468-3b072d02be9b',
 'thanos::sroute:e6158a3a-1c8d-4019-96c5-cbaf0cd4ad20',
 'thanos::sroute:1bd072d0-5dda-4c70-820c-d0c7b5f445dd',
 'thanos::sroute:29e6f66e-943c-4d69-a4b4-c189adca55c8',
 'thanos::sroute:98307aaf-1697-4b07-b916-67a669b18412',
 'thanos::sroute:44002459-ed94-4629-84ac-dbc525b82a22',
 'thanos::sroute:9b9fa11f-7204-483f-a5d1-14331a3c2b6d',
 'thanos::sroute:10ff86d0-57dc-48e6-9dd4-8ad28b9

In [0]:
route_query = f'''
select name, route_type, route_schedule_uuid, reporting_time, halt_centers_center_name, halt_centers_position, 
case when halt_centers_rel_eta not like '%day%' then 
format_datetime(from_unixtime(((hour(CAST(reporting_time AS TIME)) * 3600 + minute(CAST(reporting_time AS TIME)) * 60 + second(CAST(reporting_time AS TIME))) +(hour(CAST(halt_centers_rel_eta AS TIME)) * 3600 + minute(CAST(halt_centers_rel_eta AS TIME)) * 60 + second(CAST(halt_centers_rel_eta AS TIME))) ) % 86400), 'HH:mm:ss')
else halt_centers_rel_eta end AS arrival_time,

case when halt_centers_rel_etd not like '%day%' then 
format_datetime(from_unixtime(((hour(CAST(reporting_time AS TIME)) * 3600 + minute(CAST(reporting_time AS TIME)) * 60 + second(CAST(reporting_time AS TIME))) +(hour(CAST(halt_centers_rel_etd AS TIME)) * 3600 + minute(CAST(halt_centers_rel_etd AS TIME)) * 60 + second(CAST(halt_centers_rel_etd AS TIME))) ) % 86400), 'HH:mm:ss') 
else halt_centers_rel_etd end AS departure_time, 
halt_centers_past_travel_hrs,
halt_centers_halt_hrs as processing_time

from
(select distinct
name, route_surface_distance, route_type, route_subtype, route_schedule_uuid, route_position, route_set_id,
halt_centers_rel_eta,halt_centers_rel_etd, halt_centers_center_name,
reporting_time, is_adhoc, halt_centers_position, halt_centers_past_travel_hrs, halt_centers_halt_hrs,
continuous_connection, from_unixtime(action_date/1000000) + interval '330' minute as action_date
from hudi_db.hudi_thanos_route_parquet 
 where 
-- date(from_unixtime(action_date/1000000) + interval '330' minute) >= cast('2025-01-01' as date) and 
-- name like '%Gurgaon_Tauru_GW%' and name like '%Faridabad_MathuraRoad_GW%'
-- name like '%Gurgaon_Tauru_GW (Haryana)-Faridabad_MathuraRoad_GW (Haryana)%'
route_type not in ('Adhoc') and 
is_active = true and 
-- route_schedule_uuid in ('thanos::sroute:1a87989a-5ae4-43ab-b1a9-22129d59baf5')
 route_schedule_uuid  in {route_id_array_tup}
-- and halt_centers_rel_eta not like '%day%' and halt_centers_rel_etd not like '%day%'
)
order by  reporting_time, route_schedule_uuid, halt_centers_rel_eta
'''

In [0]:
cur = conn.cursor()
cur.execute(route_query)
columns = [desc[0] for desc in cur.description]
data = cur.fetchall()
cohort_route_df = pd.DataFrame(data, columns=columns)
cur.close()
conn.close()

In [0]:
cohort_route_df_spark = spark.createDataFrame(cohort_route_df)

cohort_route_df_spark_pivot = cohort_route_df_spark.groupby('name', 'route_type', 'route_schedule_uuid', 'reporting_time').pivot('halt_centers_position').agg(min('halt_centers_center_name').alias('halt_center'), min('arrival_time').alias('arrival_time'), min('departure_time').alias('departure_time'), min('processing_time').alias('processing_time')).fillna(0) 

# cohort_route_df_spark_pivot = cohort_route_df_spark.groupby('name', 'route_type', 'route_schedule_uuid', 'reporting_time').pivot('halt_centers_position').agg(min('arrival_time').alias('arrival_time'), min('departure_time').alias('departure_time')).fillna(0)

display(cohort_route_df_spark_pivot.orderBy(col('name'),col('reporting_time')))

# Surat_Varachha_C (Gujarat) -> Surat_Kacholi_GW (Gujarat) -> Aurangabad_Gngapr_H (Maharashtra) -> Nanded_Wajegaon_H (Maharashtra) -> Nanded_HarshNager_D (Maharashtra)

name route_type route_schedule_uuid reporting_time 0_halt_center 0_arrival_time 0_departure_time 0_processing_time 1_halt_center 1_arrival_time 1_departure_time 1_processing_time 2_halt_center 2_arrival_time 2_departure_time 2_processing_time 3_halt_center 3_arrival_time 3_departure_time 3_processing_time Carting--C1--Faridabad_MathuraRoad_GW--Gurgaon_Tauru_GW --o Carting thanos::sroute:0afd6f8e-7486-47be-b206-4fdaab21f948 04:00:00 Faridabad_MathuraRoad_GW (Haryana) 04:00:00 04:00:00 0.0 Gurgaon_Tauru_GW (Haryana) 06:30:00 11:00:00 4.5 Faridabad_MathuraRoad_GW (Haryana) 14:00:00 15:30:00 1.5 null null null 0.0 Carting--C1--Pune_Sudhwadi_GW--Pune_Kalewadi_D--Pune_Kesnand_D--o Carting thanos::sroute:c2432a9f-3cd7-430e-9b53-f2816c7f6225 04:30:00 Pune_Sudhwadi_GW (Maharashtra) 04:30:00 04:30:00 0.0 Pune_Kalewadi_D (Maharashtra) 05:30:00 06:00:00 0.5 Pune_Kesnand_D (Maharashtra) 07:30:00 08:00:00 0.5 Pune_Sudhwadi_GW (Maharashtra) 10:00:00 10:30:00 0.5 Carting--C1--Pune_Sudhwadi_GW--Pune_Kasarwadi_D--o Carting thanos::sroute:76ec74f2-8d96-4952-85a2-e92231b2210c 05:00:00 Pune_Sudhwadi_GW (Maharashtra) 05:00:00 05:00:00 0.0 Pune_Kasarwadi_D (Maharashtra) 06:00:00 06:30:00 0.5 Pune_Sudhwadi_GW (Maharashtra) 07:30:00 08:00:00 0.5 null null null 0.0 Carting--C10--Faridabad_MathuraRoad_GW--Gurgaon_Tauru_GW--o Carting thanos::sroute:e6158a3a-1c8d-4019-96c5-cbaf0cd4ad20 00:00:00 Faridabad_MathuraRoad_GW (Haryana) 00:00:00 00:00:00 0.0 Gurgaon_Tauru_GW (Haryana) 02:30:00 07:00:00 4.5 Faridabad_MathuraRoad_GW (Haryana) 09:30:00 11:30:00 2.0 null null null 0.0 Carting--C11--Faridabad_MathuraRoad_GW--Gurgaon_Tauru_GW--o Carting thanos::sroute:e3e8d18d-7644-40b4-9d35-6b28590d1091 03:00:00 Faridabad_MathuraRoad_GW (Haryana) 03:00:00 03:00:00 0.0 Gurgaon_Tauru_GW (Haryana) 05:30:00 10:00:00 4.5 Faridabad_MathuraRoad_GW (Haryana) 13:00:00 14:30:00 1.5 null null null 0.0 Carting--C13--Faridabad_MathuraRoad_GW--Gurgaon_Tauru_GW--o Carting thanos::sroute:1e652078-58d0-40a6-a8f1-68a21488efd4 05:30:00 Faridabad_MathuraRoad_GW (Haryana) 05:30:00 05:30:00 0.0 Gurgaon_Tauru_GW (Haryana) 08:00:00 10:30:00 2.5 Faridabad_MathuraRoad_GW (Haryana) 13:30:00 14:00:00 0.5 null null null 0.0 Carting--C15--Faridabad_MathuraRoad_GW--Gurgaon_Tauru_GW--o Carting thanos::sroute:99293255-3dc5-4938-8aef-e5de8c9668a9 21:00:00 Faridabad_MathuraRoad_GW (Haryana) 21:00:00 21:00:00 0.0 Gurgaon_Tauru_GW (Haryana) 23:30:00 02:00:00 2.5 Faridabad_MathuraRoad_GW (Haryana) 05:00:00 05:30:00 0.5 null null null 0.0 Carting--C17--Faridabad_MathuraRoad_GW--Gurgaon_Tauru_GW--o Carting thanos::sroute:1bd072d0-5dda-4c70-820c-d0c7b5f445dd 23:00:00 Faridabad_MathuraRoad_GW (Haryana) 23:00:00 23:00:00 0.0 Gurgaon_Tauru_GW (Haryana) 01:30:00 04:30:00 3.0 Faridabad_MathuraRoad_GW (Haryana) 07:00:00 07:30:00 0.5 null null null 0.0 Carting--C18--Faridabad_MathuraRoad_GW--Gurgaon_Tauru_GW--o Carting thanos::sroute:26baa17f-5399-48e0-a0d3-df7779cbbd4a 06:00:00 Faridabad_MathuraRoad_GW (Haryana) 06:00:00 06:00:00 0.0 Gurgaon_Tauru_GW (Haryana) 08:30:00 11:30:00 3.0 Faridabad_MathuraRoad_GW (Haryana) 14:30:00 15:00:00 0.5 null null null 0.0 Carting--C19--Faridabad_MathuraRoad_GW--Gurgaon_Tauru_GW--o Carting thanos::sroute:29e6f66e-943c-4d69-a4b4-c189adca55c8 05:00:00 Faridabad_MathuraRoad_GW (Haryana) 05:00:00 05:00:00 0.0 Gurgaon_Tauru_GW (Haryana) 07:30:00 10:30:00 3.0 Faridabad_MathuraRoad_GW (Haryana) 13:30:00 14:00:00 0.5 null null null 0.0 Carting--C2--Faridabad_MathuraRoad_GW--Gurgaon_Tauru_GW--o Carting thanos::sroute:18d9b3b7-71fe-44d2-9258-4f7fd3b7742f 01:00:00 Faridabad_MathuraRoad_GW (Haryana) 01:00:00 01:00:00 0.0 Gurgaon_Tauru_GW (Haryana) 03:30:00 09:30:00 6.0 Faridabad_MathuraRoad_GW (Haryana) 12:30:00 15:30:00 3.0 null null null 0.0 Carting--C2--Pune_Sudhwadi_GW--Pune_Kasarwadi_D--Pune_Bapodi_D--O Carting thanos::sroute:c2c0680b-bfec-4506-96ac-3c7637b1786b 11:30:00 Pune_Sudhwadi_GW (Maharashtra) 11:30:00 11:30:00 0.0 Pune_Kasarwadi_D (Maharashtra) 12:30:00 12:45:00 0.25 Pune_Bapodi

### Analyze and take Sample WBNs for cohort and trip id

In [0]:
ad_c = '2025-03-01'
query = f'''
select *, 
cast(date_diff('minute', min_scan_time, max_scan_time)/60.00 as double) as center_dwell_in_hour
from
(select   wbn,  cs_sl, 
min(cs_sd + interval '330' minute ) as min_scan_time, max(cs_sd + interval '330' minute ) as max_scan_time
from express_dwh.package_s3_parquet
    where 
    ad >= '{ad_c}'
    and cs_st = 'UD' and cs_sl != oc and cs_sl != cn
     and wbn in (select distinct wbn from  express_dwh.package_s3_parquet where ad >= '{ad_c}' and 
     trid in (select distinct  trip_uuid
from express_dwh.trips_parquet
where ad >= date_format(cast('{ad_c}' as date), '%Y-%m-%d-%H')
and  route_schedule_uuid in ('thanos::sroute:2b1486ad-ef96-468f-a171-c2379240d45a') ) ) 
       and  bzn in ('D','D1','D2') and oc like '%Surat_Varachha_C%' and cn like '%Nanded_HarshNager_D%'
     -- and  bzn in ('C','C1','C2') and oc like '%Delhi_Airport_GW%' and cn like '%Bavla_Rajoda_D%'
  --   and  bzn in ('B') and oc like '%Surat_Laldarwaja1_C%' and cn like '%Dungarpur_IrolZoneCmplx_DPP%'
     group by 1,2 )
'''

In [0]:
cur = conn.cursor()
cur.execute(query)
columns = [desc[0] for desc in cur.description]
data = cur.fetchall()
test = pd.DataFrame(data, columns=columns)
cur.close()
conn.close()

In [0]:
test_spark = spark.createDataFrame(test)
display(test_spark.orderBy(col('wbn'),col('cs_sl')))

wbn cs_sl min_scan_time max_scan_time center_dwell_in_hour 12609410849391 Aurangabad_Gngapr_H (Maharashtra) 2025-02-28 19:25:09.250 2025-03-02 05:48:54.668 34.38 12609410849391 Nanded_Wajegaon_H (Maharashtra) 2025-03-02 14:01:10.120 2025-03-03 04:27:21.795 14.43 12609410849660 Aurangabad_Gngapr_H (Maharashtra) 2025-02-28 19:27:40.253 2025-03-02 05:50:11.544 34.37 12609410849660 Nanded_Wajegaon_H (Maharashtra) 2025-03-02 14:01:10.120 2025-03-03 04:25:29.225 14.4 12609410852305 Aurangabad_Gngapr_H (Maharashtra) 2025-03-03 09:50:27.750 2025-03-04 02:09:57.503 16.32 12609410852305 Nanded_Wajegaon_H (Maharashtra) 2025-03-04 12:39:52.892 2025-03-05 04:26:25.327 15.77 12609410852305 Surat_Kacholi_GW (Gujarat) 2025-03-01 17:38:41.000 2025-03-02 20:36:42.549 26.97 12609410852832 Surat_Kacholi_GW (Gujarat) 2025-03-02 01:48:42.711 2025-03-02 01:48:43.013 0.0 13719114899926 Aurangabad_Gngapr_H (Maharashtra) 2025-03-01 17:43:08.246 2025-03-02 05:42:58.837 11.98 13719114899926 Nanded_Wajegaon_H (Maharashtra) 2025-03-02 14:01:10.120 2025-03-03 04:25:14.565 14.4 13719114925056 Aurangabad_Gngapr_H (Maharashtra) 2025-03-06 16:42:13.437 2025-03-07 05:11:50.988 12.48 13719114925056 Nanded_Wajegaon_H (Maharashtra) 2025-03-07 13:17:25.906 2025-03-08 03:23:35.027 14.1 13719114925056 Surat_Kacholi_GW (Gujarat) 2025-03-05 00:52:04.000 2025-03-06 03:33:03.196 26.67 14217118413381 Nanded_Wajegaon_H (Maharashtra) 2025-03-05 10:43:12.173 2025-03-06 03:41:15.688 16.97 14217118413381 WarangaPhata_Kalamnuri_D (Maharashtra) 2025-03-03 07:18:27.111 2025-03-05 06:24:06.799 47.08 14217118679554 Aurangabad_Gngapr_H (Maharashtra) 2025-03-07 16:13:22.706 2025-03-08 03:24:30.409 11.18 14217118679554 Nanded_Wajegaon_H (Maharashtra) 2025-03-08 16:40:01.644 2025-03-09 04:06:34.674 11.43 14217118679554 Surat_Kacholi_GW (Gujarat) 2025-03-06 20:32:48.000 2025-03-07 03:51:52.504 7.32 142285120701931 Aurangabad_Gngapr_H (Maharashtra) 2025-03-01 17:43:08.246 2025-03-02 05:31:38.660 11.8 142285120701931 Nanded_Wajegaon_H (Maharashtra) 2025-03-02 14:01:10.120 2025-03-03 04:20:05.116 14.3 142285121006630 Aurangabad_Gngapr_H (Maharashtra) 2025-03-03 09:50:27.750 2025-03-04 02:44:27.892 16.9 142285121006630 Nanded_Wajegaon_H (Maharashtra) 2025-03-04 12:39:52.892 2025-03-05 04:37:09.229 15.95 142285121006630 Surat_Kacholi_GW (Gujarat) 2025-03-01 20:26:24.109 2025-03-02 21:10:12.156 24.72 142285121039320 Aurangabad_Gngapr_H (Maharashtra) 2025-03-02 16:25:22.032 2025-03-03 00:17:05.116 7.85 142285121039320 Nanded_Wajegaon_H (Maharashtra) 2025-03-03 10:00:33.118 2025-03-04 04:45:22.437 18.73 142285121039320 Surat_Kacholi_GW (Gujarat) 2025-03-01 16:00:18.000 2025-03-02 04:28:52.703 12.47 142285121421866 Aurangabad_Gngapr_H (Maharashtra) 2025-03-05 16:40:48.201 2025-03-06 06:11:24.644 13.5 142285121421866 Nanded_Wajegaon_H (Maharashtra) 2025-03-06 16:19:04.095 2025-03-08 03:40:11.627 35.35 142285121421866 Surat_Kacholi_GW (Gujarat) 2025-03-04 02:30:55.000 2025-03-05 03:02:11.906 24.52 142285121761370 Aurangabad_Gngapr_H (Maharashtra) 2025-03-08 17:50:02.814 2025-03-09 03:40:21.252 9.83 142285121761370 Nanded_Wajegaon_H (Maharashtra) 2025-03-09 12:35:44.242 2025-03-10 04:28:26.317 15.87 142285121761370 Surat_Kacholi_GW (Gujarat) 2025-03-06 23:07:13.000 2025-03-08 03:29:29.849 28.37 142285121764601 Aurangabad_Gngapr_H (Maharashtra) 2025-03-08 17:50:02.814 2025-03-09 03:30:32.175 9.67 142285121764601 Nanded_Wajegaon_H (Maharashtra) 2025-03-09 12:35:44.242 2025-03-10 04:21:15.710 15.75 142285121764601 Surat_Kacholi_GW (Gujarat) 2025-03-07 00:21:13.000 2025-03-08 03:28:11.158 27.1 142285122287862 Aurangabad_Gngapr_H (Maharashtra) 2025-03-11 20:18:31.713 2025-03-11 23:21:43.805 3.05 142285122287862 Nanded_Wajegaon_H (Maharashtra) 2025-03-12 11:06:09.265 2025-03-12 11:06:09.265 0.0 142285122287862 Surat_Kacholi_GW (Gujarat) 2025-03-10 16:38:28.201 2025-03-11 05:58:38.756 13.33 1490810978020066 Aurangabad_Gngapr_H (Maharashtra) 2025-03-04 16:40:55.559 2025-03-05 05:06:46.885 12.42 149081097802

In [0]:
wbn_route_query = f'''
with wbn_trip_id as
(select  distinct wbn, trid trip_uuid1
from express_dwh.package_s3_parquet
    where 
    ad >= date_format(cast('{ad}' as date), '%Y-%m-%d-%H')
    -- and ad <= date_format(cast('{ad2}' as date), '%Y-%m-%d-%H')
    and date(date_cpd + interval '330' minute) >= cast('{start_date}' as date)
    and date(date_cpd + interval '330' minute) <= cast('{end_date}' as date)
    and cs_st = 'UD'
  -- and  bzn in ('D','D1','D2') and oc like '%Faridabad_MathuraRoad_GW%' and cn like '%Sasaram_Karwandiya_D%'
  --   and  bzn in ('C','C1','C2') and oc like '%Delhi_Airport_GW%' and cn like '%Bavla_Rajoda_D%'
  --  and  bzn in ('B') and oc like '%Surat_Laldarwaja1_C%' and cn like '%Dungarpur_IrolZoneCmplx_DPP%'
   and  bzn in ('A') and oc like '%Jaipur_Sez_GW%' and cn like '%Jaipur_Saktinagar_D%'
  )

select route_schedule_uuid, count(distinct wbn) as wbn_count
from
(select distinct route_schedule_uuid, trip_uuid
from express_dwh.trips_parquet
where ad >= date_format(cast('{ad}' as date), '%Y-%m-%d-%H')
and  route_schedule_uuid in ('thanos::sroute:1f8e72fd-dc44-45da-a144-66e85d224b51',
'thanos::sroute:3d076339-06e6-4385-846f-386014df8a1c')) a
left join wbn_trip_id b
on a.trip_uuid = b.trip_uuid1
group by 1
order by 2
'''

In [0]:
cur = conn.cursor()
cur.execute(wbn_route_query)
columns = [desc[0] for desc in cur.description]
data = cur.fetchall()
route_wbn_df = pd.DataFrame(data, columns=columns)
cur.close()
conn.close()

In [0]:
route_wbn_spark_df = spark.createDataFrame(route_wbn_df)
display(route_wbn_spark_df)

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-3738024149458290>, line 1
----> 1 route_wbn_spark_df = spark.createDataFrame(route_wbn_df)
      2 display(route_wbn_spark_df)

NameError: name 'route_wbn_df' is not defined

In [0]:
1

In [0]:
wbn_query = f'''
with wbn_journey as 
    ( select distinct wbn, mwn,
    trid trip_uuid,
    cs_ss as type,
    cs_sr as action_performed,
    -- date_dlvdt + interval '330' minute delivery_time, 
    cs_sd + interval '330' minute scan_time,
    cs_sl as current_scan_location,
    cs_slid as current_scan_loc_id,
    cs_nsl,
    cs_st,
    ocid,
    cnid,
    oc,
    cn,
    from_unixtime(action_date/1000000.0) + interval '330' minute action_time
    from express_dwh.package_s3_parquet
    where 
    ad >= date_format(cast('2025-02-25' as date), '%Y-%m-%d-%H')

    and wbn in ('1490810990076494',
'1490810999046316',
'1490811016267996',
'1490811029763985',
'1490810989622113',
'1490811000652190',
'1490810977140030',
'1490811000292073',
'14519126594664',
'29612817628390',
'1490811058829304',
'1490811027085870',
'142285120701931',
'1490811001182370',
'1490811010488004')
        
    order by wbn, scan_time)




select * 
from

( select 
  distinct  a.wbn, a.trip_uuid , route_schedule_uuid, a.action_performed,a.scan_time,
   current_scan_location, b.action_performed,
  from_unixtime(b.action_date/1000000.0) + interval '330' minute trip_time
   FROM
   wbn_journey a
   left join express_dwh.trips_parquet b
   on a.trip_uuid = b.trip_uuid and action_center = current_scan_loc_id

   where
   b.ad >= date_format(cast('2025-02-25' as date), '%Y-%m-%d-%H')
    and b.action_performed in ('Arrived','Departed')
    order by 1, scan_time )

      
'''

In [0]:
cur = conn.cursor()
cur.execute(wbn_query)
columns = [desc[0] for desc in cur.description]
data = cur.fetchall()
wbn_df = pd.DataFrame(data, columns=columns)
cur.close()
conn.close()

In [0]:
display(wbn_df)

wbn trip_uuid route_schedule_uuid action_performed scan_time current_scan_location action_performed trip_time 1490811001182370 trip-174093510713609867 thanos::sroute:2b1486ad-ef96-468f-a171-c2379240d45a Trip Arrived 2025-03-03 10:00:33.386 Nanded_Wajegaon_H (Maharashtra) Arrived 2025-03-03 10:00:32.300 UTC 1490811010488004 trip-174102714310047738 thanos::sroute:2b1486ad-ef96-468f-a171-c2379240d45a Trip Arrived 2025-03-04 12:39:53.215 Nanded_Wajegaon_H (Maharashtra) Arrived 2025-03-04 12:39:52.200 UTC 142285120701931 trip-174112578088211161 thanos::sroute:4f750615-27cd-4a77-bab8-7e0ed1fb2c28 Bag Added To Trip 2025-03-05 10:40:48.086 Nanded_HarshNager_D (Maharashtra) Arrived 2025-03-05 06:19:09.300 UTC 142285120701931 trip-174076663730110838 thanos::sroute:3d80936a-7cd2-4827-a642-b109aec6e5da Bag Added To Trip 2025-03-01 03:08:09.066 Surat_Kacholi_GW (Gujarat) Departed 2025-03-01 04:56:08.500 UTC 1490810989622113 trip-174095501573536401 thanos::sroute:f6d7f1c0-1017-4edb-afe5-146074cbb63e Trip Arrived 2025-03-03 06:04:38.908 Kalwar_Bhagwatinagar_D (Rajasthan) Departed 2025-03-03 07:01:21.300 UTC 1490811027085870 trip-174114477821456429 thanos::sroute:e31a1da0-42a0-4225-bb78-3808ac591af5 Bag Added To Trip 2025-03-05 10:10:03.102 Gurgaon_Tauru_GW (Haryana) Departed 2025-03-05 11:28:28.200 UTC 1490810989622113 trip-174167493993284563 thanos::sroute:25449035-f29e-481c-93e8-fe7c60a8557a Bag Added To Trip 2025-03-11 18:44:47.824 Ahmedabad_Kanera_GW (Gujarat) Departed 2025-03-11 19:37:37.500 UTC 1490811058829304 trip-174119260717414949 thanos::sroute:577069c9-d968-4fab-a86f-1de5da310d20 Bag Added To Trip 2025-03-05 22:15:11.238 Faridabad_MathuraRoad_GW (Haryana) Arrived 2025-03-05 22:06:47.200 UTC 1490811000652190 trip-174095975086615863 thanos::sroute:ee65593e-3593-48af-8fd4-8cff53961309 Bag Added To Trip 2025-03-03 05:56:20.548 Jaipur_Sez_GW (Rajasthan) Arrived 2025-03-03 05:25:50.900 UTC 1490811027085870 trip-174118991606024924 thanos::sroute:626fc629-48b7-4f7e-be14-70c557195096 Vehicle delayed 2025-03-06 08:24:00.677 Noida_DeriSkaner_H (Uttar Pradesh) Departed 2025-03-06 09:47:18.800 UTC 1490810989622113 trip-174167493993284563 thanos::sroute:25449035-f29e-481c-93e8-fe7c60a8557a Vehicle delayed - Controllable 2025-03-12 03:23:37.565 Ahmedabad_Kanera_GW (Gujarat) Departed 2025-03-11 19:37:37.500 UTC 1490811000292073 trip-174085311922754838 thanos::sroute:f3739fb0-b896-4059-8aa8-5bac6b86c336 Trip Arrived 2025-03-02 21:22:13.573 Jaipur_Sez_GW (Rajasthan) Arrived 2025-03-02 21:22:10.600 UTC 1490811000652190 trip-174104150469928102 thanos::sroute:f6d7f1c0-1017-4edb-afe5-146074cbb63e Bag Added To Trip 2025-03-04 04:18:24.998 Jaipur_RingRoad_I (Rajasthan) Arrived 2025-03-04 04:08:25.000 UTC 1490810977140030 trip-17407581626677181 thanos::sroute:f3739fb0-b896-4059-8aa8-5bac6b86c336 Bag Added To Trip 2025-02-28 22:34:10.410 Ahmedabad_Kanera_GW (Gujarat) Arrived 2025-02-28 21:26:02.700 UTC 1490811029763985 trip-174101700925753806 thanos::sroute:8141c4b4-e9a9-44d0-a5a0-a9491926d8c4 Trip Arrived 2025-03-04 06:18:12.358 Ahmedabad_Kanera_GW (Gujarat) Arrived 2025-03-04 06:18:09.800 UTC 1490811000652190 trip-174085311922754838 thanos::sroute:f3739fb0-b896-4059-8aa8-5bac6b86c336 Bag Added To Trip 2025-03-02 04:39:20.880 Ahmedabad_Kanera_GW (Gujarat) Departed 2025-03-02 04:57:14.500 UTC 1490811000292073 trip-174097718975965942 thanos::sroute:484458df-391d-4bba-b0c5-15093dd8ad80 Bag Added To Trip 2025-03-03 10:25:50.997 Jaipur_Sez_GW (Rajasthan) Arrived 2025-03-03 14:57:16.400 UTC 1490811000292073 trip-174097718975965942 thanos::sroute:484458df-391d-4bba-b0c5-15093dd8ad80 Bag Added To Trip 2025-03-03 10:25:50.997 Jaipur_Sez_GW (Rajasthan) Departed 2025-03-03 11:23:50.000 UTC 1490811001182370 trip-174093510713609867 thanos::sroute:2b1486ad-ef96-468f-a171-c2379240d45a Trip Arrived 2025-03-03 10:00:33.386 Nanded_Wajegaon_H (Maharashtra) Departed 2025-03-03 16:56:03.500 UTC 1490811027085870 trip-17411936011285235 thanos::sroute:49a0cd0b-a361-4396-b147-2d

In [0]:
all_cohorts_pd = wbn_jounery_df_spark.toPandas()

In [0]:
search = "Dhule_MohadiUpnagar_I"
all_cohorts_test = all_cohorts_pd[(all_cohorts_pd['wbn_jounrney_path'].str.contains(search)) & ((all_cohorts_pd['origin_facility_name']!= search) | (all_cohorts_pd['consignee_facility_name']!= search))]
# & (all_cohorts_pd['bzn'].isin(zone))
display(all_cohorts_test)
# all_cohorts_test

bzn origin_facility_name consignee_facility_name wbn_jounrney_path intransit_centers_and_dwell_in_hour wbn_count sum_network_speed_in_hours sum_fm_dwell_time_in_hours sum_total_trip_time_in_hours avg_network_speed fm_dwell_time_avg_speed total_avg_trip_time_ intransit_center_avg_dwell route_id_array2 trip_id_array2 B Bhiwandi_Lonad_GW Sakri_Arihantnagar_D Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Sakri_Arihantnagar_D (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) - (13.93 hours) 510 25259.14000000001 11376.140000000021 6102.979055553986 49.5277254901961 22.30615686274514 11.966625599125463 11.597921568627395 List(thanos::sroute:7b16f37b-8c75-467d-b04d-65a7cdb1dacd, thanos::sroute:ccfc0416-7c9f-47de-af89-ab75d475eed7, thanos::sroute:b8426ba6-16a9-4d49-bb2b-aa6d71272ae3) List(trip-174707420781449906, trip-174723561627781754, trip-174716756237296281, trip-17476849375196571, trip-174741017881282680, trip-174759835808566504, trip-17473356119465876, trip-174749781053037689, trip-174758043778729830, trip-174725248440610737, trip-174715075639171814, trip-174772009631035835, trip-174768147149793258, trip-174733549887938676, trip-174777644141916783, trip-174751586800994456, trip-174742636503473528) B Surat_Kacholi_GW Sakri_Arihantnagar_D Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Sakri_Arihantnagar_D (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) - (10.35 hours) ,Bhiwandi_Lonad_GW (Maharashtra) - (21.27 hours) 435 31871.75 6908.319999999998 9826.468694443953 73.2683908045977 15.881195402298845 22.589583205618283 31.640160919540158 List(thanos::sroute:308c104d-8893-4d3c-8081-33494e732a01, thanos::sroute:d29b03a7-9aff-4780-a3b1-747aed66831d, thanos::sroute:6e6c5cc2-b764-46fb-803a-594354c398a3, thanos::sroute:a6c616ad-6586-4392-8b14-823a5104c0ff, thanos::sroute:c3a695a8-d78e-44a2-be65-21cbb3ca2f8c, thanos::sroute:7b16f37b-8c75-467d-b04d-65a7cdb1dacd, thanos::sroute:b8426ba6-16a9-4d49-bb2b-aa6d71272ae3, thanos::sroute:e07dc469-7134-40c0-a058-5ad195b5ffb6, thanos::sroute:837cb0f2-d101-42f5-8e40-06abadff7169, thanos::sroute:ccfc0416-7c9f-47de-af89-ab75d475eed7, thanos::sroute:9bdada0a-5621-4afe-a65e-7246023e06c8, thanos::sroute:a02dc1f7-a955-4a99-a5d1-6f2d9538e447, thanos::sroute:8be3796d-545c-4f3d-b613-3fd9838d915b) List(trip-174759835808566504, trip-174750701966079440, trip-174733549887938676, trip-174749700114811556, trip-174721747570770522, trip-174706981126786819, trip-174751586800994456, trip-174772009631035835, trip-174723561627781754, trip-17476849375196571, trip-174725421810731223, trip-174758043778729830, trip-174731730883974244, trip-174746501989025904, trip-174712961615271348, trip-174742636503473528, trip-174739963397930615, trip-174738871970667115, trip-17473356119465876, trip-174749781053037689, trip-174716488979266530, trip-174725248440610737, trip-174768147149793258, trip-174777644141916783, trip-174713962049899556, trip-174703543901685800, trip-174741017881282680, trip-174758738800877381, trip-174715075639171814) B Bhiwandi_Lonad_GW Shindkheda_Patan_D Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Shindkheda_Patan_D (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) - (10.93 hours) 427 20155.81000000002 9507.499999999993 5348.734111112081 47.20330210772838 22.26580796252926 12.526309393705109 10.92723653395784 List(thanos::sroute:ccfc0416-7c9f-47de-af89-ab75d475eed7, thanos::sroute:89bb5d64-533d-492b-af74-4b6952bb2220) List(trip-174733870066805180, trip-174707420781449906, trip-174723561627781754, trip-174741017881282680, trip-17471685053342571, trip-17473356119465876, trip-174749781053037689, trip-174751663686449767, trip-174760293381348705, trip-174758043778729830, trip-174715075639171814, trip-17476846714617335, trip-174777665189178718, trip-174725257196992616, trip-174768147149793258, trip-174742606902614757) B Surat_Laldarwaja1_C Dhule_MohadiUpnagar_D Surat_Laldarwaja1_C (Gujarat) -> Surat_Kacholi

In [0]:
import re

def extract_hours(text, location = search):
    # pattern = rf"{re.escape(location)} - \(([\d.]+) hours\)"
    pattern = rf"{location}.*?\(([\d.]+) hours\)"
    if isinstance(text, str):
        match = re.search(pattern, text)
        return match.group(1) if match else None
    return None

In [0]:
all_cohorts_test["tc_dwell"] = all_cohorts_test["intransit_centers_and_dwell_in_hour"].apply(lambda x: extract_hours(x))

display(all_cohorts_test)

/root/.ipykernel/1303/command-3372277684153870-3124091966:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  all_cohorts_test["tc_dwell"] = all_cohorts_test["intransit_centers_and_dwell_in_hour"].apply(lambda x: extract_hours(x))


bzn origin_facility_name consignee_facility_name wbn_jounrney_path intransit_centers_and_dwell_in_hour wbn_count sum_network_speed_in_hours sum_fm_dwell_time_in_hours sum_total_trip_time_in_hours avg_network_speed fm_dwell_time_avg_speed total_avg_trip_time_ intransit_center_avg_dwell route_id_array2 trip_id_array2 tc_dwell B Bhiwandi_Lonad_GW Sakri_Arihantnagar_D Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Sakri_Arihantnagar_D (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) - (13.93 hours) 510 25259.14000000001 11376.140000000021 6102.979055553986 49.5277254901961 22.30615686274514 11.966625599125463 11.597921568627395 List(thanos::sroute:7b16f37b-8c75-467d-b04d-65a7cdb1dacd, thanos::sroute:ccfc0416-7c9f-47de-af89-ab75d475eed7, thanos::sroute:b8426ba6-16a9-4d49-bb2b-aa6d71272ae3) List(trip-174707420781449906, trip-174723561627781754, trip-174716756237296281, trip-17476849375196571, trip-174741017881282680, trip-174759835808566504, trip-17473356119465876, trip-174749781053037689, trip-174758043778729830, trip-174725248440610737, trip-174715075639171814, trip-174772009631035835, trip-174768147149793258, trip-174733549887938676, trip-174777644141916783, trip-174751586800994456, trip-174742636503473528) 13.93 B Surat_Kacholi_GW Sakri_Arihantnagar_D Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Sakri_Arihantnagar_D (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) - (10.35 hours) ,Bhiwandi_Lonad_GW (Maharashtra) - (21.27 hours) 435 31871.75 6908.319999999998 9826.468694443953 73.2683908045977 15.881195402298845 22.589583205618283 31.640160919540158 List(thanos::sroute:308c104d-8893-4d3c-8081-33494e732a01, thanos::sroute:d29b03a7-9aff-4780-a3b1-747aed66831d, thanos::sroute:6e6c5cc2-b764-46fb-803a-594354c398a3, thanos::sroute:a6c616ad-6586-4392-8b14-823a5104c0ff, thanos::sroute:c3a695a8-d78e-44a2-be65-21cbb3ca2f8c, thanos::sroute:7b16f37b-8c75-467d-b04d-65a7cdb1dacd, thanos::sroute:b8426ba6-16a9-4d49-bb2b-aa6d71272ae3, thanos::sroute:e07dc469-7134-40c0-a058-5ad195b5ffb6, thanos::sroute:837cb0f2-d101-42f5-8e40-06abadff7169, thanos::sroute:ccfc0416-7c9f-47de-af89-ab75d475eed7, thanos::sroute:9bdada0a-5621-4afe-a65e-7246023e06c8, thanos::sroute:a02dc1f7-a955-4a99-a5d1-6f2d9538e447, thanos::sroute:8be3796d-545c-4f3d-b613-3fd9838d915b) List(trip-174759835808566504, trip-174750701966079440, trip-174733549887938676, trip-174749700114811556, trip-174721747570770522, trip-174706981126786819, trip-174751586800994456, trip-174772009631035835, trip-174723561627781754, trip-17476849375196571, trip-174725421810731223, trip-174758043778729830, trip-174731730883974244, trip-174746501989025904, trip-174712961615271348, trip-174742636503473528, trip-174739963397930615, trip-174738871970667115, trip-17473356119465876, trip-174749781053037689, trip-174716488979266530, trip-174725248440610737, trip-174768147149793258, trip-174777644141916783, trip-174713962049899556, trip-174703543901685800, trip-174741017881282680, trip-174758738800877381, trip-174715075639171814) 10.35 B Bhiwandi_Lonad_GW Shindkheda_Patan_D Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Shindkheda_Patan_D (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) - (10.93 hours) 427 20155.81000000002 9507.499999999993 5348.734111112081 47.20330210772838 22.26580796252926 12.526309393705109 10.92723653395784 List(thanos::sroute:ccfc0416-7c9f-47de-af89-ab75d475eed7, thanos::sroute:89bb5d64-533d-492b-af74-4b6952bb2220) List(trip-174733870066805180, trip-174707420781449906, trip-174723561627781754, trip-174741017881282680, trip-17471685053342571, trip-17473356119465876, trip-174749781053037689, trip-174751663686449767, trip-174760293381348705, trip-174758043778729830, trip-174715075639171814, trip-17476846714617335, trip-174777665189178718, trip-174725257196992616, trip-174768147149793258, trip-174742606902614757) 10.93 B Surat_Laldarwaja1_C Dhule_MohadiUpnagar_D Surat_Laldarwaja1_C

In [0]:
def split_loc(path, mid_center = search):
    parts = path.split(' -> ') 
    # return parts, mid_center

    try:
        idx = [i for i, loc in enumerate(parts) if mid_center in loc][0]
    except IndexError:
        return None, None
    
    before = parts[idx - 1] if idx > 0 else None
    current = parts[idx]
    after = parts[idx + 1] if idx < len(parts) - 1 else None

    return pd.Series({'before': before, 'target': current, 'after': after})


In [0]:
all_cohorts_test[['ptc', 'tc', 'ntc']] = all_cohorts_test['wbn_jounrney_path'].apply(split_loc)
all_cohorts_test = all_cohorts_test[['bzn', 'origin_facility_name','consignee_facility_name','wbn_jounrney_path','ptc', 'tc', 'ntc', 'wbn_count','tc_dwell']]
display(all_cohorts_test)


/root/.ipykernel/1303/command-569074101418592-756943243:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  all_cohorts_test[['ptc', 'tc', 'ntc']] = all_cohorts_test['wbn_jounrney_path'].apply(split_loc)
/root/.ipykernel/1303/command-569074101418592-756943243:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  all_cohorts_test[['ptc', 'tc', 'ntc']] = all_cohorts_test['wbn_jounrney_path'].apply(split_loc)
/root/.ipykernel/1303/command-569074101418592-756943243:1: SettingWithCopyWarning: 
A value is trying to be se

bzn origin_facility_name consignee_facility_name wbn_jounrney_path ptc tc ntc wbn_count tc_dwell B Bhiwandi_Lonad_GW Sakri_Arihantnagar_D Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Sakri_Arihantnagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Sakri_Arihantnagar_D (Maharashtra) 510 13.93 B Surat_Kacholi_GW Sakri_Arihantnagar_D Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Sakri_Arihantnagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Sakri_Arihantnagar_D (Maharashtra) 435 10.35 B Bhiwandi_Lonad_GW Shindkheda_Patan_D Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Shindkheda_Patan_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Shindkheda_Patan_D (Maharashtra) 427 10.93 B Surat_Laldarwaja1_C Dhule_MohadiUpnagar_D Surat_Laldarwaja1_C (Gujarat) -> Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Dhule_MohadiUpnagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Dhule_MohadiUpnagar_D (Maharashtra) 397 75.76 B Surat_Varachha_C Satana_MitraNagar_D Surat_Varachha_C (Gujarat) -> Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Satana_MitraNagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Satana_MitraNagar_D (Maharashtra) 391 10.63 B Bhiwandi_Lonad_GW Satana_MitraNagar_D Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Satana_MitraNagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Satana_MitraNagar_D (Maharashtra) 390 10.87 B Bhiwandi_Lonad_GW Dhule_MohadiUpnagar_D Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Dhule_MohadiUpnagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Dhule_MohadiUpnagar_D (Maharashtra) 389 53.05 B Surat_Laldarwaja1_C Satana_MitraNagar_D Surat_Laldarwaja1_C (Gujarat) -> Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Satana_MitraNagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Satana_MitraNagar_D (Maharashtra) 380 10.62 B Surat_RingRd_C Satana_MitraNagar_D Surat_RingRd_C (Gujarat) -> Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Satana_MitraNagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Satana_MitraNagar_D (Maharashtra) 379 10.79 B Bhiwandi_Lonad_GW Malegaon_ValmikNagar_D Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Malegaon_ValmikNagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Malegaon_ValmikNagar_D (Maharashtra) 355 10.39 B Surat_Varachha_C Dhule_MohadiUpnagar_D Surat_Varachha_C (Gujarat) -> Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Dhule_MohadiUpnagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Dhule_MohadiUpnagar_D (Maharashtra) 329 80.50 B Surat_Laldarwaja1_C Shindkheda_Patan_D Surat_Laldarwaja1_C (Gujarat) -> Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Shindkheda_Patan_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Shindkheda_Patan_D (Maharashtra) 311 10.78 B Surat_Varachha_C Shindkheda_Patan_D Surat_Varachha_C (Gujarat) -> Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Shindkheda_Patan_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Shindkheda_Patan_D (Maharashtra) 306 10.79 B Surat_Laldarwaja1_C Shirpur_KrantiNgr_D S

In [0]:
route_query = f'''
select name, route_type, route_schedule_uuid, reporting_time, halt_centers_center_name, halt_centers_position, 
-- case when halt_centers_rel_eta not like '%day%' then  format_datetime(from_unixtime(((hour(CAST(reporting_time AS TIME)) * 3600 + minute(CAST(reporting_time AS TIME)) * 60 + second(CAST(reporting_time AS TIME))) +(hour(CAST(halt_centers_rel_eta AS TIME)) * 3600 + minute(CAST(halt_centers_rel_eta AS TIME)) * 60 + second(CAST(halt_centers_rel_eta AS TIME))) ) % 86400), 'HH:mm:ss') else 

halt_centers_rel_eta  AS arrival_time,

-- case when halt_centers_rel_etd not like '%day%' then format_datetime(from_unixtime(((hour(CAST(reporting_time AS TIME)) * 3600 + minute(CAST(reporting_time AS TIME)) * 60 + second(CAST(reporting_time AS TIME))) +(hour(CAST(halt_centers_rel_etd AS TIME)) * 3600 + minute(CAST(halt_centers_rel_etd AS TIME)) * 60 + second(CAST(halt_centers_rel_etd AS TIME))) ) % 86400), 'HH:mm:ss')  else 

halt_centers_rel_etd  AS departure_time, 
halt_centers_past_travel_hrs,
halt_centers_halt_hrs as processing_time

from
(select distinct
name, route_surface_distance, route_type, route_subtype, route_schedule_uuid, route_position, route_set_id,
halt_centers_rel_eta,halt_centers_rel_etd, halt_centers_center_name,
reporting_time, is_adhoc, halt_centers_position, halt_centers_past_travel_hrs, halt_centers_halt_hrs,
continuous_connection, from_unixtime(action_date/1000000) + interval '330' minute as action_date
from hudi_db.hudi_thanos_route_parquet 
 where 
 -- date(from_unixtime(action_date/1000000) + interval '330' minute) >= cast('2024-01-01' as date) and 
route_type not in ('Adhoc') and 
is_active = true  
)
order by  reporting_time, route_schedule_uuid, halt_centers_rel_eta
'''

In [0]:
# cur = conn.cursor()
# cur.execute(route_query)
# columns = [desc[0] for desc in cur.description]
# data = cur.fetchall()
# cohort_route_df = pd.DataFrame(data, columns=columns)
# cur.close()
# conn.close()


In [0]:

# print(cohort_route_df.shape)
# display(cohort_route_df)

In [0]:
from itertools import combinations

def tranform_data(df):
    
    num_stops = len([col for col in df.columns if "_halt_center" in col])
    transformed_data = []
    for _, row in df.iterrows():
        for i, j in combinations(range(num_stops), 2):
            transformed_data.append({
                "route_name": row["name"],
                "route_id": row["route_schedule_uuid"],
                "oc_reporting_time": row["reporting_time"],
                "origin": row[f"{i}_halt_center"],
                "destination": row[f"{j}_halt_center"],
                "origin_arrival": row[f"{i}_arrival_time"],
                "origin_departure": row[f"{i}_departure_time"],
                "origin_processing": row[f"{i}_processing_time"],
                "destination_arrival": row[f"{j}_arrival_time"],
                "destination_departure": row[f"{j}_departure_time"],
                "destination_processing": row[f"{j}_processing_time"] })

    output_df = pd.DataFrame(transformed_data)
    output_df = output_df[(output_df['origin'].notna()) & (output_df['destination'].notna())].reset_index(drop = True)
    output_df = output_df.sort_values("origin_departure")
    output_df_agg = output_df.groupby(["origin", "destination"]).agg(list).reset_index()

    return output_df_agg

def convert_to_hours(time_str):
    td = pd.to_timedelta(time_str)
    total_seconds = td.total_seconds()
    hours = int(total_seconds // 3600)
    minutes = int((total_seconds % 3600) // 60)
    seconds = int(total_seconds % 60)
    return f"{hours:02}:{minutes:02}:{seconds:02}"

def to_24_hour(td):
    total_seconds = int(td.total_seconds())
    hours = (total_seconds // 3600) % 24
    minutes = (total_seconds % 3600) // 60
    seconds = total_seconds % 60
    return f"{hours:02}:{minutes:02}:{seconds:02}"

# Apply conversion to convert 1day 2:00 types to 26:00:00
cohort_route_df['arrival_time_clean'] = cohort_route_df['arrival_time'].apply(convert_to_hours)
cohort_route_df['departure_time_clean'] = cohort_route_df['departure_time'].apply(convert_to_hours)


cohort_route_df['reporting_td'] = pd.to_timedelta(cohort_route_df['reporting_time'])
cohort_route_df['arrival_td'] = pd.to_timedelta(cohort_route_df['arrival_time_clean'])
cohort_route_df['departure_td'] = pd.to_timedelta(cohort_route_df['departure_time_clean'])


# Add both time to reporting time
cohort_route_df['final_arrival_td'] = cohort_route_df['reporting_td'] + cohort_route_df['arrival_td']
cohort_route_df['final_departure_td'] = cohort_route_df['reporting_td'] + cohort_route_df['departure_td']

#convert back to 24 hour format
cohort_route_df['arrival_time_1'] = cohort_route_df['final_arrival_td'].apply(to_24_hour)
cohort_route_df['departure_time_1'] = cohort_route_df['final_departure_td'].apply(to_24_hour)

cohort_route_df = cohort_route_df[['name', 'route_type', 'route_schedule_uuid', 'reporting_time',
       'halt_centers_center_name', 'halt_centers_position', 'arrival_time_1', 'departure_time_1', 'halt_centers_past_travel_hrs', 'processing_time']]

cohort_route_df_spark = spark.createDataFrame(cohort_route_df)

cohort_route_df_spark_pivot = cohort_route_df_spark.groupby('name', 'route_type', 'route_schedule_uuid', 'reporting_time').pivot('halt_centers_position').agg(min('halt_centers_center_name').alias('halt_center'), min('arrival_time_1').alias('arrival_time'), min('departure_time_1').alias('departure_time'), min('processing_time').alias('processing_time')).fillna(0) 


all_conn_pd = cohort_route_df_spark_pivot.toPandas()

test_output = tranform_data(all_conn_pd)

print(test_output.shape)
display(test_output)

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-5976153302059740>, line 45
     42     return f"{hours:02}:{minutes:02}:{seconds:02}"
     44 # Apply conversion to convert 1day 2:00 types to 26:00:00
---> 45 cohort_route_df['arrival_time_clean'] = cohort_route_df['arrival_time'].apply(convert_to_hours)
     46 cohort_route_df['departure_time_clean'] = cohort_route_df['departure_time'].apply(convert_to_hours)
     49 cohort_route_df['reporting_td'] = pd.to_timedelta(cohort_route_df['reporting_time'])

NameError: name 'cohort_route_df' is not defined

In [0]:
# delhivery_connection_data = "/dbfs/FileStore/all_OD_pair_connection_array.parquet" 
# # test_output.to_parquet(delhivery_connection_data)
# print(delhivery_connection_data)

In [0]:
delhivery_connection_data = "/dbfs/FileStore/all_OD_pair_connection_array.parquet" 

test_output2 = pd.read_parquet(delhivery_connection_data)

In [0]:
display(test_output2[(test_output2['origin']=='Ahmednagar_Nagapur_H (Maharashtra)') & (test_output2['destination']== 'Newasa_Khurd_D (Maharashtra)')])

	


origin destination route_name route_id oc_reporting_time origin_arrival origin_departure origin_processing destination_arrival destination_departure destination_processing Ahmednagar_Nagapur_H (Maharashtra) Newasa_Khurd_D (Maharashtra) List(bid-Secondary-Ahmednagar-Newasa-Rahuri-Ahmednagar, bid-Secondary-Ahmednagar-Newasa-Rahuri-Ahmednagar, Carting--Ahmednagar_Nagapur_H--Newasa_Khurd_D--Loni_BailBzr_DPP--o) List(thanos::sroute:b1405b33-da12-4c45-a725-e6e30d2634e2, thanos::sroute:8932215c-357d-4d23-96aa-da8678ce10e1, thanos::sroute:14bf5687-50e7-46b2-8ed7-944ce8afa637) List(03:00:00, 03:00:00, 04:00:00) List(03:00:00, 03:00:00, 04:00:00) List(04:00:00, 04:00:00, 04:00:00) List(1.0, 1.0, 0.0) List(06:30:00, 06:30:00, 06:00:00) List(07:00:00, 07:00:00, 06:30:00) List(0.5, 0.5, 0.5)

In [0]:
dwell_connection_df = all_cohorts_test.merge(test_output2, left_on=['ptc','tc'], right_on=['origin','destination'], how='inner')
dwell_connection_df2 = dwell_connection_df.merge(test_output2, left_on=['tc','ntc'], right_on=['origin','destination'], how='left')

dwell_connection_df3 = dwell_connection_df2[['bzn', 'origin_facility_name', 'consignee_facility_name','wbn_jounrney_path', 'ptc', 'tc', 'ntc', 'wbn_count','tc_dwell','oc_reporting_time_x','origin_departure_x','destination_arrival_x','destination_processing_x','oc_reporting_time_y','origin_departure_y','destination_arrival_y']].rename(columns = {'oc_reporting_time_x':'ptc_reporting_time','origin_departure_x':'ptc_departure','destination_arrival_x':'tc_arrival','destination_processing_x':'tc_processing_time','oc_reporting_time_y':'tc_reporting_time','origin_departure_y':'tc_departure','destination_arrival_y':'ntc_arrival'})


In [0]:
display(dwell_connection_df3)

bzn origin_facility_name consignee_facility_name wbn_jounrney_path ptc tc ntc wbn_count tc_dwell ptc_reporting_time ptc_departure tc_arrival tc_processing_time tc_reporting_time tc_departure ntc_arrival B Bhiwandi_Lonad_GW Sakri_Arihantnagar_D Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Sakri_Arihantnagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Sakri_Arihantnagar_D (Maharashtra) 510 13.93 List(04:30:00) List(07:00:00) List(15:45:00) List(2.5) List(04:00:00) List(04:00:00) List(05:30:00) B Surat_Kacholi_GW Sakri_Arihantnagar_D Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Sakri_Arihantnagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Sakri_Arihantnagar_D (Maharashtra) 435 10.35 List(04:30:00) List(07:00:00) List(15:45:00) List(2.5) List(04:00:00) List(04:00:00) List(05:30:00) B Bhiwandi_Lonad_GW Shindkheda_Patan_D Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Shindkheda_Patan_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Shindkheda_Patan_D (Maharashtra) 427 10.93 List(04:30:00) List(07:00:00) List(15:45:00) List(2.5) List(04:00:00) List(04:00:00) List(05:30:00) B Surat_Laldarwaja1_C Dhule_MohadiUpnagar_D Surat_Laldarwaja1_C (Gujarat) -> Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Dhule_MohadiUpnagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Dhule_MohadiUpnagar_D (Maharashtra) 397 75.76 List(04:30:00) List(07:00:00) List(15:45:00) List(2.5) null null null B Surat_Varachha_C Satana_MitraNagar_D Surat_Varachha_C (Gujarat) -> Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Satana_MitraNagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Satana_MitraNagar_D (Maharashtra) 391 10.63 List(04:30:00) List(07:00:00) List(15:45:00) List(2.5) List(04:00:00) List(04:00:00) List(07:30:00) B Bhiwandi_Lonad_GW Satana_MitraNagar_D Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Satana_MitraNagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Satana_MitraNagar_D (Maharashtra) 390 10.87 List(04:30:00) List(07:00:00) List(15:45:00) List(2.5) List(04:00:00) List(04:00:00) List(07:30:00) B Bhiwandi_Lonad_GW Dhule_MohadiUpnagar_D Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Dhule_MohadiUpnagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Dhule_MohadiUpnagar_D (Maharashtra) 389 53.05 List(04:30:00) List(07:00:00) List(15:45:00) List(2.5) null null null B Surat_Laldarwaja1_C Satana_MitraNagar_D Surat_Laldarwaja1_C (Gujarat) -> Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Satana_MitraNagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Satana_MitraNagar_D (Maharashtra) 380 10.62 List(04:30:00) List(07:00:00) List(15:45:00) List(2.5) List(04:00:00) List(04:00:00) List(07:30:00) B Surat_RingRd_C Satana_MitraNagar_D Surat_RingRd_C (Gujarat) -> Surat_Kacholi_GW (Gujarat) -> Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Satana_MitraNagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Satana_MitraNagar_D (Maharashtra) 379 10.79 List(04:30:00) List(07:00:00) List(15:45:00) List(2.5) List(04:00:00) List(04:00:00) List(07:30:00) B Bhiwandi_Lonad_GW Malegaon_ValmikNagar_D Bhiwandi_Lonad_GW (Maharashtra) -> Dhule_MohadiUpnagar_I (Maharashtra) -> Malegaon_ValmikNagar_D (Maharashtra) Bhiwandi_Lonad_GW (Maharashtra) Dhule_MohadiUpnagar_I (Maharashtra) Malegaon_ValmikNagar_D (Maharashtra) 355 10.39 List(04:30:00) List(07:00:00) List(15:45:00) List(2.5) List(